In [1]:
import numpy as np
import pandas as pd
import gc
import os
import hickle as hkl
from numpy import random
from sklearn.preprocessing import MinMaxScaler

from sklearn.preprocessing import LabelEncoder
from sklearn.externals import joblib

from keras.models import Model
from keras.optimizers import Adam, SGD
from keras import initializers, regularizers, constraints
from keras.layers import Bidirectional, GlobalMaxPooling1D, Dense, Embedding
from keras.layers import concatenate, Input, LSTM, GRU, merge, Lambda, Dot, Add, Multiply, \
wrappers, Dropout, GlobalAveragePooling1D, Bidirectional, BatchNormalization, Activation
import tensorflow as tf
from keras.models import Sequential
from keras.layers.core import Reshape
import keras.backend as K
from keras.engine.topology import Layer
from keras.layers import LSTM, Dense
from tqdm import tqdm
import glob
from keras.callbacks import EarlyStopping, ModelCheckpoint, Callback, ReduceLROnPlateau

#from keras_contrib.layers import CRF

import keras.backend as KTF
import tensorflow as tf
#os.environ["CUDA_VISIBLE_DEVICES"] = "1"
config = tf.ConfigProto()
config.gpu_options.allow_growth = True
sess = tf.Session(config=config)
KTF.set_session(sess)

data_path = 'Skip_Data/'


Using TensorFlow backend.


In [2]:
(2+1.5+1.5)/3

1.6666666666666667

In [2]:

batch_size = 1500 # skip_net_glove_max_mtsk_more_layer_best

batch_size = 3000 # skip_net_glove_max_mtsk_more_layer_best_v2

batch_size = 3000 # skip_net_glove_max_mtsk_more_layer_best_bn

batch_size = 2200 # skip_net_glove_max_mtsk_more_layer_best_v3

batch_size = 2200 # skip_net_glove_max_mtsk_more_layer_best_v4



data_path = 'Skip_Data/'

le_track_id = joblib.load('le_track_id.pkl')

spotify_song_fea = pd.read_parquet('spotify_song_fea.parquet')

le = LabelEncoder()
##
spotify_song_fea['mode'] = le.fit_transform(spotify_song_fea['mode'])

track_id = np.array(spotify_song_fea['track_id'])

cols_to_be_normalized = ['duration', 'release_year', 'us_popularity_estimate',
       'acousticness', 'beat_strength', 'bounciness', 'danceability',
       'dyn_range_mean', 'energy', 'flatness', 'instrumentalness', 'key',
       'liveness', 'loudness', 'mechanism', 'mode', 'organism', 'speechiness',
       'tempo', 'time_signature', 'valence', 'acoustic_vector_0',
       'acoustic_vector_1', 'acoustic_vector_2', 'acoustic_vector_3',
       'acoustic_vector_4', 'acoustic_vector_5', 'acoustic_vector_6',
       'acoustic_vector_7']

scaler = MinMaxScaler()

spotify_song_array = scaler.fit_transform(spotify_song_fea[cols_to_be_normalized])

order = np.argsort(track_id)
spotify_song_array = spotify_song_array[order,:]

/usr/local/lib/python3.5/dist-packages/sklearn/base.py:251: UserWarning: Trying to unpickle estimator LabelEncoder from version 0.20.1 when using version 0.20.0. This might lead to breaking code or invalid results. Use at your own risk.
  UserWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


In [16]:

batch_size = 1500 # skip_net_glove_max_mtsk_more_layer_best

batch_size = 3000 # skip_net_glove_max_mtsk_more_layer_best_v2

batch_size = 3000 # skip_net_glove_max_mtsk_more_layer_best_bn

data_path = 'Skip_Data/'

le_track_id = joblib.load('le_track_id.pkl')

spotify_song_fea = pd.read_parquet('spotify_song_fea.parquet')

le = LabelEncoder()
##
spotify_song_fea['mode'] = le.fit_transform(spotify_song_fea['mode'])

track_id = np.array(spotify_song_fea['track_id'])

spotify_song_fea['duration'] = spotify_song_fea['duration']/100
spotify_song_fea['release_year'] = spotify_song_fea['release_year']-1950
spotify_song_fea['us_popularity_estimate'] = spotify_song_fea['us_popularity_estimate'] - 90

spotify_song_fea['duration_05'] = spotify_song_fea['duration']**0.5
spotify_song_fea['duration_15'] = spotify_song_fea['duration']**1.5
spotify_song_fea['duration_2'] = spotify_song_fea['duration']**2
spotify_song_fea['duration_3'] = spotify_song_fea['duration']**3

spotify_song_fea['release_year_05'] = spotify_song_fea['release_year']**0.5
spotify_song_fea['release_year_15'] = spotify_song_fea['release_year']**1.5
spotify_song_fea['release_year_2'] = spotify_song_fea['release_year']**2
spotify_song_fea['release_year_3'] = spotify_song_fea['release_year']**3

spotify_song_fea['us_popularity_estimate_15'] = spotify_song_fea['us_popularity_estimate']**1.5
spotify_song_fea['us_popularity_estimate_2'] = spotify_song_fea['us_popularity_estimate']**2
spotify_song_fea['us_popularity_estimate_3'] = spotify_song_fea['us_popularity_estimate']**3

cols_to_be_normalized = ['us_popularity_estimate_3', 'us_popularity_estimate_2', 'us_popularity_estimate_15', 'release_year_05','release_year_15','release_year_2','duration_05','duration_15','duration_2','duration', 'release_year', 'us_popularity_estimate',
       'acousticness', 'beat_strength', 'bounciness', 'danceability',
       'dyn_range_mean', 'energy', 'flatness', 'instrumentalness', 'key',
       'liveness', 'loudness', 'mechanism', 'mode', 'organism', 'speechiness',
       'tempo', 'time_signature', 'valence', 'acoustic_vector_0',
       'acoustic_vector_1', 'acoustic_vector_2', 'acoustic_vector_3',
       'acoustic_vector_4', 'acoustic_vector_5', 'acoustic_vector_6',
       'acoustic_vector_7']

scaler = MinMaxScaler()

spotify_song_array = scaler.fit_transform(spotify_song_fea[cols_to_be_normalized])

order = np.argsort(track_id)
spotify_song_array = spotify_song_array[order,:]

/usr/local/lib/python3.5/dist-packages/sklearn/base.py:251: UserWarning: Trying to unpickle estimator LabelEncoder from version 0.20.1 when using version 0.20.0. This might lead to breaking code or invalid results. Use at your own risk.
  UserWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


In [3]:
song_zero_embedding = -2*np.ones((1,spotify_song_array.shape[1]))
spotify_song_array = np.concatenate((song_zero_embedding,spotify_song_array),axis=0)

In [5]:
spotify_song_array_glove = hkl.load('song_embedding_matrix_150.hkl')

#order = np.arange(spotify_song_array.shape[0])
#random.shuffle(order)

#spotify_song_array_glove = spotify_song_array_glove[order,:]


gc.collect()

spotify_song_array = np.concatenate((spotify_song_array,spotify_song_array_glove),axis=1)

In [6]:
spotify_song_array.shape

(3706389, 179)

In [15]:
#from sklearn.externals import joblib
#joblib.dump(le_context_type, data_path+'le_context_type.pkl')
#joblib.dump(le_reason_start, data_path+'le_reason_start.pkl')
#joblib.dump(le_reason_end, data_path+'le_reason_end.pkl')

['Skip_Data/le_reason_end.pkl']

In [7]:
le_context_type = joblib.load(data_path+'le_context_type.pkl')
le_reason_start = joblib.load(data_path+'le_reason_start.pkl')
le_reason_end = joblib.load(data_path+'le_reason_end.pkl')

n_context_type = len(le_context_type.classes_) + 1
n_reason_start = len(le_reason_start.classes_) + 1
n_reason_end = len(le_reason_end.classes_) + 1

In [7]:

def ProcessSessionCate(df, if_gen = 0, batch_size = batch_size):
    df['context_type'] = le_context_type.transform(df['context_type'])
    df['hist_user_behavior_reason_start'] = le_reason_start.transform(df['hist_user_behavior_reason_start'])
    df['hist_user_behavior_reason_end'] = le_reason_end.transform(df['hist_user_behavior_reason_end'])
    session_cols = ['session_id', 'session_position', 'session_length', 'track_id_clean',
                    'skip_1', 'skip_2', 'skip_3', 'not_skipped', 'context_switch',
                    'no_pause_before_play', 'short_pause_before_play',
                    'long_pause_before_play', 'hist_user_behavior_n_seekfwd',
                    'hist_user_behavior_n_seekback', 'hist_user_behavior_is_shuffle',
                    'hour_of_day', 'premium', 'context_type',
                    'hist_user_behavior_reason_start', 'hist_user_behavior_reason_end']

    df['track_id_clean'] = df['track_id_clean'] + 1
    df['hour_of_day'] = df['hour_of_day']/24
    
    n0 = df.shape[0]

    raw_data = np.array(df[session_cols].values) * 1
    raw_data = raw_data.astype(np.float)

    input_raw_data = raw_data[raw_data[:,1] * 2 <= raw_data[:, 2], :]
    output_raw_data = raw_data[raw_data[:,1] * 2 > raw_data[:, 2], :]

    input_raw_data_final_p = np.floor(input_raw_data[:, 2] / 2).astype(np.int)
    input_raw_data_final_p = 10 - input_raw_data_final_p + input_raw_data[:, 1]

    output_raw_data_first_p = np.floor(output_raw_data[:, 2] / 2).astype(np.int)
    output_raw_data_first_p = -output_raw_data_first_p + output_raw_data[:, 1]

    n_session = int(np.max(raw_data[:,0])) + 1
    gc.collect()
    input_data = -2 * np.ones((n_session * 10, 18))
    output_data = -2 * np.ones((n_session * 10, 18))

    input_data[:, 17] = n_reason_end - 1
    output_data[:, 17] = n_reason_end - 1
    
    input_data[:, 16] = n_reason_start - 1
    output_data[:, 16] = n_reason_start - 1
    
    input_data[:, 15] = n_context_type - 1
    output_data[:, 15] = n_context_type - 1
    
    '''
    
    output_premium = input_data[:,9,14]    
    output_premium = np.reshape(output_premium,(len(output_premium),1,1))
    output_premium = np.tile(output_premium,(1,10,1))
    '''
    
    input_raw_data[:,2] = input_raw_data[:,1]/input_raw_data[:,2]
    output_raw_data[:,2] = output_raw_data[:,1]/output_raw_data[:,2]


    input_data[input_raw_data[:, 0].astype(np.int) * 10 + input_raw_data_final_p.astype(np.int) - 1,
    :] = input_raw_data[:, 2:20]
    output_data[output_raw_data[:, 0].astype(np.int) * 10 + output_raw_data_first_p.astype(np.int) - 1,
    :] = output_raw_data[:, 2:20]
    input_data = np.reshape(input_data, (n_session, 10, input_data.shape[1]))
    output_data = np.reshape(output_data, (n_session, 10, output_data.shape[1]))
    output_data_target = output_data[:, :, 2:10]
    output_data_target[output_data_target < 0] = 0
    
    #output_data_target[:,:,3] = 1 - output_data_target[:,:,1]   
    
    output_data_id = output_data[:,:,1]

    order = np.arange(n_session)
    random.shuffle(order)
    
    if if_gen == 1:
        order = order[0:int(batch_size*np.floor(n_session/batch_size))]        

    input_data = input_data[order,:,:]  
 
    input_data_context_id = input_data[:,:,15]
    input_data_start_id = input_data[:,:,16]
    input_data_end_id = input_data[:,:,17]

    input_data = input_data[:,:,range(15)]

    input_data_id = input_data[:,:,1]
    input_data = np.delete(input_data, 1, 2)
    output_data_id = output_data_id[order,:]
    output_data_target = output_data_target[order,:]
    
    output_data = output_data[:,:,0]
    
    input_data_context_id[input_data_context_id<0] = 0
    input_data_start_id[input_data_start_id<0] = 0
    input_data_end_id[input_data_end_id<0] = 0
    input_data_id[input_data_id<0] = 0
    output_data_id[output_data_id<0] = 0
    
    input_data_context_id = input_data_context_id.astype(int)
    input_data_start_id = input_data_start_id.astype(int)
    input_data_end_id = input_data_end_id.astype(int)
    input_data_id = input_data_id.astype(int)
    output_data_id = output_data_id.astype(int)

    return input_data, output_data, input_data_context_id, input_data_start_id, input_data_end_id,\
           input_data_id, output_data_id, output_data_target

In [14]:
#For v4

elements = [-2,-1,0,1,2]
probabilities = [0.1,0.25,0.3,0.25,0.1]
#np.random.choice(elements, 10, p=probabilities)

def ProcessSessionCate(df, if_gen = 0, batch_size = batch_size, sample = 0):
    df['context_type'] = le_context_type.transform(df['context_type'])
    df['hist_user_behavior_reason_start'] = le_reason_start.transform(df['hist_user_behavior_reason_start'])
    df['hist_user_behavior_reason_end'] = le_reason_end.transform(df['hist_user_behavior_reason_end'])
    session_cols = ['session_id', 'session_position', 'session_length', 'track_id_clean',
                    'skip_1', 'skip_2', 'skip_3', 'not_skipped', 'context_switch',
                    'no_pause_before_play', 'short_pause_before_play',
                    'long_pause_before_play', 'hist_user_behavior_n_seekfwd',
                    'hist_user_behavior_n_seekback', 'hist_user_behavior_is_shuffle',
                    'hour_of_day', 'premium', 'context_type',
                    'hist_user_behavior_reason_start', 'hist_user_behavior_reason_end']
    
    session_id = np.unique(df['session_id'])    
    session_position_offset = np.random.choice(elements, len(session_id), p=probabilities)
    df_offset = pd.DataFrame()
    df_offset['session_id'] = session_id
    if sample == 1:
        df_offset['session_position_offset'] = session_position_offset
    else:
        df_offset['session_position_offset'] = 0
        
    n0 = df.shape[0]

        
    df = pd.merge(df, df_offset, on = 'session_id', how = 'left')
    df['session_position'] = df['session_position'] + df['session_position_offset']
    df = df[df['session_position']<=df['session_length']].reset_index(drop=True)
    df = df[df['session_position']>=1].reset_index(drop=True)
    
    n1 = df.shape[0]
    
    #print('shrinkage:',n0, n1)


    df['track_id_clean'] = df['track_id_clean'] + 1
    df['hour_of_day'] = df['hour_of_day']/24

    raw_data = np.array(df[session_cols].values) * 1
    raw_data = raw_data.astype(np.float)

    input_raw_data = raw_data[raw_data[:,1] * 2 <= raw_data[:, 2], :]
    output_raw_data = raw_data[raw_data[:,1] * 2 > raw_data[:, 2], :]

    input_raw_data_final_p = np.floor(input_raw_data[:, 2] / 2).astype(np.int)
    input_raw_data_final_p = 10 - input_raw_data_final_p + input_raw_data[:, 1]

    output_raw_data_first_p = np.floor(output_raw_data[:, 2] / 2).astype(np.int)
    output_raw_data_first_p = -output_raw_data_first_p + output_raw_data[:, 1]

    n_session = int(np.max(raw_data[:,0])) + 1
    gc.collect()
    input_data = -2 * np.ones((n_session * 10, 18))
    output_data = -2 * np.ones((n_session * 10, 18))

    input_data[:, 17] = n_reason_end - 1
    output_data[:, 17] = n_reason_end - 1
    
    input_data[:, 16] = n_reason_start - 1
    output_data[:, 16] = n_reason_start - 1
    
    input_data[:, 15] = n_context_type - 1
    output_data[:, 15] = n_context_type - 1
    
    '''
    
    output_premium = input_data[:,9,14]    
    output_premium = np.reshape(output_premium,(len(output_premium),1,1))
    output_premium = np.tile(output_premium,(1,10,1))
    '''
    
    input_raw_data[:,2] = input_raw_data[:,1]/input_raw_data[:,2]
    output_raw_data[:,2] = output_raw_data[:,1]/output_raw_data[:,2]


    input_data[input_raw_data[:, 0].astype(np.int) * 10 + input_raw_data_final_p.astype(np.int) - 1,
    :] = input_raw_data[:, 2:20]
    output_data[output_raw_data[:, 0].astype(np.int) * 10 + output_raw_data_first_p.astype(np.int) - 1,
    :] = output_raw_data[:, 2:20]
    input_data = np.reshape(input_data, (n_session, 10, input_data.shape[1]))
    output_data = np.reshape(output_data, (n_session, 10, output_data.shape[1]))
    output_data_target = output_data[:, :, 2:13]
    output_data_target[output_data_target>1] = 1
    output_data_target[output_data_target < 0] = 0
    
    #output_data_target[:,:,3] = 1 - output_data_target[:,:,1]   
    
    output_data_id = output_data[:,:,1]

    order = np.arange(n_session)
    random.shuffle(order)
    
    if if_gen == 1:
        order = order[0:int(batch_size*np.floor(n_session/batch_size))]        

    input_data = input_data[order,:,:]  
 
    input_data_context_id = input_data[:,:,15]
    input_data_start_id = input_data[:,:,16]
    input_data_end_id = input_data[:,:,17]

    input_data = input_data[:,:,range(15)]

    input_data_id = input_data[:,:,1]
    input_data = np.delete(input_data, 1, 2)
    output_data_id = output_data_id[order,:]
    output_data_target = output_data_target[order,:]
    
    output_data = output_data[:,:,0]
    
    input_data_context_id[input_data_context_id<0] = 0
    input_data_start_id[input_data_start_id<0] = 0
    input_data_end_id[input_data_end_id<0] = 0
    input_data_id[input_data_id<0] = 0
    output_data_id[output_data_id<0] = 0
    
    input_data_context_id = input_data_context_id.astype(int)
    input_data_start_id = input_data_start_id.astype(int)
    input_data_end_id = input_data_end_id.astype(int)
    input_data_id = input_data_id.astype(int)
    output_data_id = output_data_id.astype(int)

    return input_data, output_data, input_data_context_id, input_data_start_id, input_data_end_id,\
           input_data_id, output_data_id, output_data_target

In [ ]:
#For v5

elements = [-2,-1,0,1,2]
probabilities = [0.1,0.25,0.3,0.25,0.1]
#np.random.choice(elements, 10, p=probabilities)

def ProcessSessionCate(df, if_gen = 0, batch_size = batch_size, sample = 0):
     df['date'] = pd.to_datetime(df['date'] )
        
    df['date_gap'] = df['date'] - pd.Timestamp(2018, 7, 13)
    df['date_gap'] = df['date_gap'].dt.days
    
    
    df['context_type'] = le_context_type.transform(df['context_type'])
    df['hist_user_behavior_reason_start'] = le_reason_start.transform(df['hist_user_behavior_reason_start'])
    df['hist_user_behavior_reason_end'] = le_reason_end.transform(df['hist_user_behavior_reason_end'])
    session_cols = ['session_id', 'session_position', 'session_length', 'track_id_clean',
                    'skip_1', 'skip_2', 'skip_3', 'not_skipped', 'context_switch',
                    'no_pause_before_play', 'short_pause_before_play',
                    'long_pause_before_play', 'hist_user_behavior_n_seekfwd',
                    'hist_user_behavior_n_seekback', 'hist_user_behavior_is_shuffle',
                    'hour_of_day', 'premium', 'context_type',
                    'hist_user_behavior_reason_start', 'hist_user_behavior_reason_end','date_gap']
    
    session_id = np.unique(df['session_id'])    
    session_position_offset = np.random.choice(elements, len(session_id), p=probabilities)
    df_offset = pd.DataFrame()
    df_offset['session_id'] = session_id
    if sample == 1:
        df_offset['session_position_offset'] = session_position_offset
    else:
        df_offset['session_position_offset'] = 0
        
    n0 = df.shape[0]

        
    df = pd.merge(df, df_offset, on = 'session_id', how = 'left')
    df['session_position'] = df['session_position'] + df['session_position_offset']
    df = df[df['session_position']<=df['session_length']].reset_index(drop=True)
    df = df[df['session_position']>=1].reset_index(drop=True)
    
    n1 = df.shape[0]
    
    #print('shrinkage:',n0, n1)

    df['track_id_clean'] = df['track_id_clean'] + 1
    df['hour_of_day'] = df['hour_of_day']/24

    raw_data = np.array(df[session_cols].values) * 1
    raw_data = raw_data.astype(np.float)

    input_raw_data = raw_data[raw_data[:,1] * 2 <= raw_data[:, 2], :]
    output_raw_data = raw_data[raw_data[:,1] * 2 > raw_data[:, 2], :]

    input_raw_data_final_p = np.floor(input_raw_data[:, 2] / 2).astype(np.int)
    input_raw_data_final_p = 10 - input_raw_data_final_p + input_raw_data[:, 1]

    output_raw_data_first_p = np.floor(output_raw_data[:, 2] / 2).astype(np.int)
    output_raw_data_first_p = -output_raw_data_first_p + output_raw_data[:, 1]

    n_session = int(np.max(raw_data[:,0])) + 1
    gc.collect()
    input_data = -2 * np.ones((n_session * 10, 18))
    output_data = -2 * np.ones((n_session * 10, 19))

    input_data[:, 17] = n_reason_end - 1
    output_data[:, 17] = n_reason_end - 1
    
    input_data[:, 16] = n_reason_start - 1
    output_data[:, 16] = n_reason_start - 1
    
    input_data[:, 15] = n_context_type - 1
    output_data[:, 15] = n_context_type - 1
    
    '''
    
    output_premium = input_data[:,9,14]    
    output_premium = np.reshape(output_premium,(len(output_premium),1,1))
    output_premium = np.tile(output_premium,(1,10,1))
    '''
    
    input_raw_data[:,2] = input_raw_data[:,1]/input_raw_data[:,2]
    output_raw_data[:,2] = output_raw_data[:,1]/output_raw_data[:,2]


    input_data[input_raw_data[:, 0].astype(np.int) * 10 + input_raw_data_final_p.astype(np.int) - 1,
    :] = input_raw_data[:, 2:20]
    output_data[output_raw_data[:, 0].astype(np.int) * 10 + output_raw_data_first_p.astype(np.int) - 1,
    :] = output_raw_data[:, 2:21]
    input_data = np.reshape(input_data, (n_session, 10, input_data.shape[1]))
    output_data = np.reshape(output_data, (n_session, 10, output_data.shape[1]))
    output_data_target = output_data[:, :, 2:13]
    output_data_target[output_data_target>1] = 1
    output_data_target[output_data_target < 0] = 0
    
    output_date_id = output_data[:, :, 18]
    
    #output_data_target[:,:,3] = 1 - output_data_target[:,:,1]   
    
    output_data_id = output_data[:,:,1]

    order = np.arange(n_session)
    random.shuffle(order)
    
    if if_gen == 1:
        order = order[0:int(batch_size*np.floor(n_session/batch_size))]        

    input_data = input_data[order,:,:]  
 
    input_data_context_id = input_data[:,:,15]
    input_data_start_id = input_data[:,:,16]
    input_data_end_id = input_data[:,:,17]

    input_data = input_data[:,:,range(15)]

    input_data_id = input_data[:,:,1]
    input_data = np.delete(input_data, 1, 2)
    output_data_id = output_data_id[order,:]
    output_data_target = output_data_target[order,:]
    
    output_data = output_data[:,:,0]
    
    input_data_context_id[input_data_context_id<0] = 0
    input_data_start_id[input_data_start_id<0] = 0
    input_data_end_id[input_data_end_id<0] = 0
    input_data_id[input_data_id<0] = 0
    output_data_id[output_data_id<0] = 0
    
    input_data_context_id = input_data_context_id.astype(int)
    input_data_start_id = input_data_start_id.astype(int)
    input_data_end_id = input_data_end_id.astype(int)
    input_data_id = input_data_id.astype(int)
    output_data_id = output_data_id.astype(int)

    return input_data, output_data, input_data_context_id, input_data_start_id, input_data_end_id,\
           input_data_id, output_data_id, output_data_target, output_date_id

In [9]:
#for v3


def ProcessSessionCate(df, if_gen = 0, batch_size = batch_size):
    df['context_type'] = le_context_type.transform(df['context_type'])
    df['hist_user_behavior_reason_start'] = le_reason_start.transform(df['hist_user_behavior_reason_start'])
    df['hist_user_behavior_reason_end'] = le_reason_end.transform(df['hist_user_behavior_reason_end'])
    session_cols = ['session_id', 'session_position', 'session_length', 'track_id_clean',
                    'skip_1', 'skip_2', 'skip_3', 'not_skipped', 'context_switch',
                    'no_pause_before_play', 'short_pause_before_play',
                    'long_pause_before_play', 'hist_user_behavior_n_seekfwd',
                    'hist_user_behavior_n_seekback', 'hist_user_behavior_is_shuffle',
                    'hour_of_day', 'premium', 'context_type',
                    'hist_user_behavior_reason_start', 'hist_user_behavior_reason_end']

    df['track_id_clean'] = df['track_id_clean'] + 1
    df['hour_of_day'] = df['hour_of_day']/24

    raw_data = np.array(df[session_cols].values) * 1
    raw_data = raw_data.astype(np.float)

    input_raw_data = raw_data[raw_data[:,1] * 2 <= raw_data[:, 2], :]
    output_raw_data = raw_data[raw_data[:,1] * 2 > raw_data[:, 2], :]

    input_raw_data_final_p = np.floor(input_raw_data[:, 2] / 2).astype(np.int)
    input_raw_data_final_p = 10 - input_raw_data_final_p + input_raw_data[:, 1]

    output_raw_data_first_p = np.floor(output_raw_data[:, 2] / 2).astype(np.int)
    output_raw_data_first_p = -output_raw_data_first_p + output_raw_data[:, 1]

    n_session = int(np.max(raw_data[:,0])) + 1
    gc.collect()
    input_data = -2 * np.ones((n_session * 10, 18))
    output_data = -2 * np.ones((n_session * 10, 18))

    input_data[:, 17] = n_reason_end - 1
    output_data[:, 17] = n_reason_end - 1
    
    input_data[:, 16] = n_reason_start - 1
    output_data[:, 16] = n_reason_start - 1
    
    input_data[:, 15] = n_context_type - 1
    output_data[:, 15] = n_context_type - 1
    
    '''
    
    output_premium = input_data[:,9,14]    
    output_premium = np.reshape(output_premium,(len(output_premium),1,1))
    output_premium = np.tile(output_premium,(1,10,1))
    '''
    
    input_raw_data[:,2] = input_raw_data[:,1]/input_raw_data[:,2]
    output_raw_data[:,2] = output_raw_data[:,1]/output_raw_data[:,2]


    input_data[input_raw_data[:, 0].astype(np.int) * 10 + input_raw_data_final_p.astype(np.int) - 1,
    :] = input_raw_data[:, 2:20]
    output_data[output_raw_data[:, 0].astype(np.int) * 10 + output_raw_data_first_p.astype(np.int) - 1,
    :] = output_raw_data[:, 2:20]
    input_data = np.reshape(input_data, (n_session, 10, input_data.shape[1]))
    output_data = np.reshape(output_data, (n_session, 10, output_data.shape[1]))
    output_data_target = output_data[:, :, 2:13]
    output_data_target[output_data_target>1] = 1
    output_data_target[output_data_target < 0] = 0
    
    #output_data_target[:,:,3] = 1 - output_data_target[:,:,1]   
    
    output_data_id = output_data[:,:,1]

    order = np.arange(n_session)
    random.shuffle(order)
    
    if if_gen == 1:
        order = order[0:int(batch_size*np.floor(n_session/batch_size))]        

    input_data = input_data[order,:,:]  
 
    input_data_context_id = input_data[:,:,15]
    input_data_start_id = input_data[:,:,16]
    input_data_end_id = input_data[:,:,17]

    input_data = input_data[:,:,range(15)]

    input_data_id = input_data[:,:,1]
    input_data = np.delete(input_data, 1, 2)
    output_data_id = output_data_id[order,:]
    output_data_target = output_data_target[order,:]
    
    output_data = output_data[:,:,0]
    
    input_data_context_id[input_data_context_id<0] = 0
    input_data_start_id[input_data_start_id<0] = 0
    input_data_end_id[input_data_end_id<0] = 0
    input_data_id[input_data_id<0] = 0
    output_data_id[output_data_id<0] = 0
    
    input_data_context_id = input_data_context_id.astype(int)
    input_data_start_id = input_data_start_id.astype(int)
    input_data_end_id = input_data_end_id.astype(int)
    input_data_id = input_data_id.astype(int)
    output_data_id = output_data_id.astype(int)

    return input_data, output_data, input_data_context_id, input_data_start_id, input_data_end_id,\
           input_data_id, output_data_id, output_data_target

In [ ]:
'''
def ProcessSessionCate(df, if_gen = 0, batch_size = batch_size):
    df['context_type'] = le_context_type.transform(df['context_type'])
    df['hist_user_behavior_reason_start'] = le_reason_start.transform(df['hist_user_behavior_reason_start'])
    df['hist_user_behavior_reason_end'] = le_reason_end.transform(df['hist_user_behavior_reason_end'])
    session_cols = ['session_id', 'session_position', 'session_length', 'track_id_clean',
                    'skip_1', 'skip_2', 'skip_3', 'not_skipped', 'context_switch',
                    'no_pause_before_play', 'short_pause_before_play',
                    'long_pause_before_play', 'hist_user_behavior_n_seekfwd',
                    'hist_user_behavior_n_seekback', 'hist_user_behavior_is_shuffle',
                    'hour_of_day', 'premium', 'context_type',
                    'hist_user_behavior_reason_start', 'hist_user_behavior_reason_end']

    df['track_id_clean'] = df['track_id_clean'] + 1
    df['hour_of_day'] = df['hour_of_day']/24

    raw_data = np.array(df[session_cols].values) * 1
    raw_data = raw_data.astype(np.float)

    input_raw_data = raw_data[raw_data[:,1] * 2 <= raw_data[:, 2], :]
    output_raw_data = raw_data[raw_data[:,1] * 2 > raw_data[:, 2], :]

    input_raw_data_final_p = np.floor(input_raw_data[:, 2] / 2).astype(np.int)
    input_raw_data_final_p = 10 - input_raw_data_final_p + input_raw_data[:, 1]

    output_raw_data_first_p = np.floor(output_raw_data[:, 2] / 2).astype(np.int)
    output_raw_data_first_p = -output_raw_data_first_p + output_raw_data[:, 1]

    n_session = int(np.max(raw_data[:,0])) + 1
    gc.collect()
    input_data = -2 * np.ones((n_session * 10, 18))
    output_data = -2 * np.ones((n_session * 10, 18))

    input_data[:, 17] = n_reason_end - 1
    output_data[:, 17] = n_reason_end - 1
    
    input_data[:, 16] = n_reason_start - 1
    output_data[:, 16] = n_reason_start - 1
    
    input_data[:, 15] = n_context_type - 1
    output_data[:, 15] = n_context_type - 1

    output_premium = input_data[:,9,14]    
    output_premium = np.reshape(output_premium,(len(output_premium),1,1))
    output_premium = np.tile(output_premium,(1,10,1))
    
    input_raw_data[:,2] = input_raw_data[:,1]/input_raw_data[:,2]
    output_raw_data[:,2] = output_raw_data[:,1]/output_raw_data[:,2]

    input_data[input_raw_data[:, 0].astype(np.int) * 10 + input_raw_data_final_p.astype(np.int) - 1,
    :] = input_raw_data[:, 2:20]
    output_data[output_raw_data[:, 0].astype(np.int) * 10 + output_raw_data_first_p.astype(np.int) - 1,
    :] = output_raw_data[:, 2:20]
    input_data = np.reshape(input_data, (n_session, 10, input_data.shape[1]))
    output_data = np.reshape(output_data, (n_session, 10, output_data.shape[1]))
    output_data_target = output_data[:, :, 2:10]
    output_data_target[output_data_target < 0] = 0
    
    #output_data_target[:,:,3] = 1 - output_data_target[:,:,1]   
    
    output_data_id = output_data[:,:,1]

    order = np.arange(n_session)
    random.shuffle(order)
    
    if if_gen == 1:
        order = order[0:int(batch_size*np.floor(n_session/batch_size))]        

    input_data = input_data[order,:,:]  
 
    input_data_context_id = input_data[:,:,15]
    input_data_start_id = input_data[:,:,16]
    input_data_end_id = input_data[:,:,17]

    input_data = input_data[:,:,range(15)]

    input_data_id = input_data[:,:,1]
    input_data = np.delete(input_data, 1, 2)
    output_data_id = output_data_id[order,:]
    output_data_target = output_data_target[order,:]
    
    output_data = output_data[:,:,0]
    
    input_data_context_id[input_data_context_id<0] = 0
    input_data_start_id[input_data_start_id<0] = 0
    input_data_end_id[input_data_end_id<0] = 0
    input_data_id[input_data_id<0] = 0
    output_data_id[output_data_id<0] = 0
    
    input_data_context_id = input_data_context_id.astype(int)
    input_data_start_id = input_data_start_id.astype(int)
    input_data_end_id = input_data_end_id.astype(int)
    input_data_id = input_data_id.astype(int)
    output_data_id = output_data_id.astype(int)

    return input_data, output_data, input_data_context_id, input_data_start_id, input_data_end_id,\
           input_data_id, output_data_id, output_data_target, output_premium

In [15]:


#order = np.arange(spotify_song_array.shape[0])
#random.shuffle(order)

#spotify_song_array = spotify_song_array[order,:]

#order

array([1332537, 3566287, 2853096, ...,  732329, 1105170, 1727569])

In [9]:
train_files = glob.glob(data_path + '*.csv.parquet')
len(train_files)

650

In [10]:
valid_files = ['Skip_Data/log_0_20180715_000000000000.csv.parquet']
train_files = list(set(train_files)-set(valid_files))
len(train_files)

649

In [11]:
train_files

['Skip_Data/log_9_20180718_000000000000.csv.parquet',
 'Skip_Data/log_7_20180825_000000000000.csv.parquet',
 'Skip_Data/log_1_20180914_000000000000.csv.parquet',
 'Skip_Data/log_5_20180815_000000000000.csv.parquet',
 'Skip_Data/log_3_20180906_000000000000.csv.parquet',
 'Skip_Data/log_3_20180916_000000000000.csv.parquet',
 'Skip_Data/log_4_20180726_000000000000.csv.parquet',
 'Skip_Data/log_3_20180824_000000000000.csv.parquet',
 'Skip_Data/log_1_20180825_000000000000.csv.parquet',
 'Skip_Data/log_7_20180803_000000000000.csv.parquet',
 'Skip_Data/log_8_20180829_000000000000.csv.parquet',
 'Skip_Data/log_9_20180823_000000000000.csv.parquet',
 'Skip_Data/log_3_20180722_000000000000.csv.parquet',
 'Skip_Data/log_6_20180901_000000000000.csv.parquet',
 'Skip_Data/log_1_20180726_000000000000.csv.parquet',
 'Skip_Data/log_2_20180829_000000000000.csv.parquet',
 'Skip_Data/log_2_20180818_000000000000.csv.parquet',
 'Skip_Data/log_1_20180830_000000000000.csv.parquet',
 'Skip_Data/log_0_20180823_0

In [12]:

def train_generate(batch_size=batch_size, shuffle=True):
    while 1:
        c = [ i for i in range(len(train_files))]
        if shuffle:
            random.shuffle(c)
        j = 0
        X_train_i = []
        Y_train_i = []
        
        for i in c:
            #print(train_files[i])
            
            tmp_data = pd.read_parquet(train_files[i])
            input_data_i, output_data_i, input_data_context_id_i, input_data_start_id_i, input_data_end_id_i, \
            input_data_id_i, output_data_id_i, output_data_target_i = ProcessSessionCate(tmp_data,if_gen = 1, batch_size = batch_size, sample = 1)      
            
            n_round = int(input_data_i.shape[0]/batch_size)            
            
            for j in range(n_round):           
                X_train_i = {
                           'context': input_data_context_id_i[j * batch_size:(j + 1) * batch_size],
                            'start': input_data_start_id_i[j * batch_size:(j + 1) * batch_size],
                            'end': input_data_end_id_i[j * batch_size:(j + 1) * batch_size],
                            'input_fea': input_data_i[j * batch_size:(j + 1) * batch_size],
                             'output_fea': output_data_i[j * batch_size:(j + 1) * batch_size],
                            'input_id': input_data_id_i[j * batch_size:(j + 1) * batch_size],
                            'output_id': output_data_id_i[j * batch_size:(j + 1) * batch_size],
                        }                
                
                Y_train_i = output_data_target_i[j * batch_size:(j + 1) * batch_size]
                
                yield (X_train_i,Y_train_i)

In [15]:
count = 0
for file in valid_files:
    tmp_data = pd.read_parquet(file)
    input_data_i, output_data_i, input_data_context_id_i, input_data_start_id_i, input_data_end_id_i, \
    input_data_id_i, output_data_id_i, output_data_target_i = ProcessSessionCate(tmp_data)

    if count == 0:
        valid_input = input_data_i
        valid_output = output_data_i
        valid_input_id = input_data_id_i
        valid_input_data_context_id = input_data_context_id_i
        valid_input_data_start_id = input_data_start_id_i
        valid_input_data_end_id = input_data_end_id_i
        valid_output_id = output_data_id_i
        valid_target = output_data_target_i
    else:
        valid_input = np.concatenate((valid_input,input_data_i),axis=0)
        valid_output = np.concatenate((valid_output,output_data_i),axis=0)
        valid_input_data_context_id = np.concatenate((valid_input_data_context_id,input_data_context_id_i),axis=0)
        valid_input_data_start_id = np.concatenate((valid_input_data_start_id,input_data_start_id_i),axis=0)
        valid_input_data_end_id = np.concatenate((valid_input_data_end_id,input_data_end_id_i),axis=0)
        valid_input_id = np.concatenate((valid_input_id,input_data_id_i),axis=0)
        valid_output_id = np.concatenate((valid_output_id,output_data_id_i),axis=0)
        valid_target = np.concatenate((valid_target,output_data_target_i),axis=0)

    count  = count + 1

In [16]:
input_fea_dim = valid_input.shape[2]

In [17]:
spotify_song_array.shape

(3706389, 179)

In [18]:
X_valid = {
   'context': valid_input_data_context_id,
    'start': valid_input_data_start_id,
    'end': valid_input_data_end_id,
    'input_fea': valid_input,
     'output_fea': valid_output,
    'input_id': valid_input_id,
    'output_id': valid_output_id,
}

Y_valid = valid_target

hkl.dump(Y_valid, data_path+'Y_valid.hkl', mode='w', compression='gzip')

hkl.dump(valid_output, data_path+'valid_output.hkl', mode='w', compression='gzip')

In [14]:


class ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return
    
reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)


/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '


In [102]:
#double data
model.fit(
        X_train, Y_train, epochs=15, batch_size=600, verbose=1,validation_data=(X_valid,Y_valid),callbacks=[ndcg_callback(),reduceLROnPlat])

Train on 1519624 samples, validate on 178342 samples
Epoch 1/15
1519624/1519624 [==============================] - 62s 41us/step - loss: 0.5221 - binary_crossentropy: 0.5221 - binary_accuracy: 0.7138 - val_loss: 0.5214 - val_binary_crossentropy: 0.5214 - val_binary_accuracy: 0.7147
0.7036488377829693
Epoch 2/15
1519624/1519624 [==============================] - 61s 40us/step - loss: 0.5058 - binary_crossentropy: 0.5058 - binary_accuracy: 0.7271 - val_loss: 0.5111 - val_binary_crossentropy: 0.5111 - val_binary_accuracy: 0.7243
0.7146186996835414
Epoch 3/15
1519624/1519624 [==============================] - 60s 40us/step - loss: 0.5006 - binary_crossentropy: 0.5006 - binary_accuracy: 0.7314 - val_loss: 0.5087 - val_binary_crossentropy: 0.5087 - val_binary_accuracy: 0.7258
0.7160941434709139
Epoch 4/15
1519624/1519624 [==============================] - 63s 41us/step - loss: 0.4979 - binary_crossentropy: 0.4979 - binary_accuracy: 0.7333 - val_loss: 0.5068 - val_binary_crossentropy: 0.5068 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (1.117339). Check your callbacks.
  % delta_t_median)
/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.559288). Check your callbacks.
  % delta_t_median)


1519624/1519624 [==============================] - 59s 39us/step - loss: 0.4909 - binary_crossentropy: 0.4909 - binary_accuracy: 0.7389 - val_loss: 0.5041 - val_binary_crossentropy: 0.5041 - val_binary_accuracy: 0.7298
0.7204657310537056
Epoch 12/15
1519624/1519624 [==============================] - 56s 37us/step - loss: 0.4904 - binary_crossentropy: 0.4904 - binary_accuracy: 0.7393 - val_loss: 0.5032 - val_binary_crossentropy: 0.5032 - val_binary_accuracy: 0.7306
0.721298100324901

Epoch 00012: ReduceLROnPlateau reducing learning rate to 0.0004000000189989805.
Epoch 13/15
1519624/1519624 [==============================] - 59s 39us/step - loss: 0.4895 - binary_crossentropy: 0.4895 - binary_accuracy: 0.7400 - val_loss: 0.5036 - val_binary_crossentropy: 0.5036 - val_binary_accuracy: 0.7299
0.7206141328651311
Epoch 14/15
1519624/1519624 [==============================] - 63s 41us/step - loss: 0.4890 - binary_crossentropy: 0.4890 - binary_accuracy: 0.7404 - val_loss: 0.5033 - val_binary_cr

In [95]:
#80
model.fit(
        X_train, Y_train, epochs=15, batch_size=600, verbose=1,validation_data=(X_valid,Y_valid),callbacks=[ndcg_callback(),reduceLROnPlat])

Train on 777995 samples, validate on 178342 samples
Epoch 1/15
777995/777995 [==============================] - 41s 52us/step - loss: 0.5289 - binary_crossentropy: 0.5289 - binary_accuracy: 0.7085 - val_loss: 0.5284 - val_binary_crossentropy: 0.5284 - val_binary_accuracy: 0.7091
0.6978545715013119
Epoch 2/15
777995/777995 [==============================] - 33s 43us/step - loss: 0.5147 - binary_crossentropy: 0.5147 - binary_accuracy: 0.7191 - val_loss: 0.5207 - val_binary_crossentropy: 0.5207 - val_binary_accuracy: 0.7152
0.7043354434971645
Epoch 3/15
777995/777995 [==============================] - 32s 41us/step - loss: 0.5062 - binary_crossentropy: 0.5062 - binary_accuracy: 0.7268 - val_loss: 0.5124 - val_binary_crossentropy: 0.5124 - val_binary_accuracy: 0.7235
0.7133595927590469
Epoch 4/15
777995/777995 [==============================] - 32s 41us/step - loss: 0.5023 - binary_crossentropy: 0.5023 - binary_accuracy: 0.7300 - val_loss: 0.5117 - val_binary_crossentropy: 0.5117 - val_bin

In [62]:
model.fit(
        X_train, Y_train, epochs=15, batch_size=600, verbose=1,validation_data=(X_valid,Y_valid),callbacks=[ndcg_callback(),reduceLROnPlat])

Train on 777995 samples, validate on 178342 samples
Epoch 1/15
777995/777995 [==============================] - 45s 58us/step - loss: 0.5292 - binary_crossentropy: 0.5292 - binary_accuracy: 0.7081 - val_loss: 0.5294 - val_binary_crossentropy: 0.5294 - val_binary_accuracy: 0.7077
0.6975122579896238
Epoch 2/15
777995/777995 [==============================] - 61s 78us/step - loss: 0.5161 - binary_crossentropy: 0.5161 - binary_accuracy: 0.7177 - val_loss: 0.5218 - val_binary_crossentropy: 0.5218 - val_binary_accuracy: 0.7137
0.7025902381948008
Epoch 3/15
777995/777995 [==============================] - 51s 66us/step - loss: 0.5116 - binary_crossentropy: 0.5116 - binary_accuracy: 0.7209 - val_loss: 0.5191 - val_binary_crossentropy: 0.5191 - val_binary_accuracy: 0.7156
0.7045260573793954
Epoch 4/15
777995/777995 [==============================] - 50s 64us/step - loss: 0.5094 - binary_crossentropy: 0.5094 - binary_accuracy: 0.7227 - val_loss: 0.5186 - val_binary_crossentropy: 0.5186 - val_bin

In [56]:
np.mean(Y_valid)

0.44083109979701923

In [79]:
def list_min_max_normalization(X):
    min_tmp = K.min(X, axis=1, keepdims=True) - 1e-4
    max_tmp = K.max(X, axis=1, keepdims=True) + 1e-4
    gap_tmp = max_tmp - min_tmp
    gap_tmp = K.pow(gap_tmp, -1)
    X = X - min_tmp
    X = X * gap_tmp
    return X

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X

#K.clear_session()

def skip_model_2(cell_size = 200):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,10)
    reason_start_emb_layer = Embedding(n_reason_start,10)
    reason_end_emb_layer = Embedding(n_reason_end,10)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
    rnn_layer = GRU(cell_size) (input_data_a)
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_result_n = Lambda(list_min_max_normalization)(output_result)
    
    output_result = concatenate([output_result_n, output_result])

    output_result = Dense(256, activation='elu')(output_result)
    output_result = Dense(80, activation='elu')(output_result)
    output_result = Dropout(0.2)(output_result)

    output_result = Dense(1, activation='sigmoid')(output_result)
    
    output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'acc'])
    model.summary()
    return model


In [19]:
train_input_data_context_id

array([[5., 5., 5., ..., 5., 5., 5.],
       [4., 4., 4., ..., 4., 4., 4.],
       [4., 4., 4., ..., 4., 4., 4.],
       ...,
       [5., 5., 5., ..., 5., 5., 5.],
       [6., 6., 6., ..., 5., 5., 5.],
       [6., 6., 6., ..., 0., 0., 0.]])

In [20]:
train_input_data_context_id[3:10,:]

array([[6., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       [5., 5., 5., 5., 5., 5., 5., 5., 5., 5.],
       [6., 6., 6., 6., 6., 5., 5., 5., 5., 5.],
       [6., 6., 5., 5., 5., 5., 5., 5., 5., 5.],
       [6., 6., 6., 6., 6., 0., 0., 0., 0., 0.],
       [2., 2., 2., 2., 2., 2., 2., 2., 2., 2.],
       [6., 6., 6., 6., 0., 0., 0., 0., 0., 0.]])

In [21]:
train_input_data_context_id[3:20,:]

array([[6., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       [5., 5., 5., 5., 5., 5., 5., 5., 5., 5.],
       [6., 6., 6., 6., 6., 5., 5., 5., 5., 5.],
       [6., 6., 5., 5., 5., 5., 5., 5., 5., 5.],
       [6., 6., 6., 6., 6., 0., 0., 0., 0., 0.],
       [2., 2., 2., 2., 2., 2., 2., 2., 2., 2.],
       [6., 6., 6., 6., 0., 0., 0., 0., 0., 0.],
       [6., 6., 6., 6., 3., 3., 3., 3., 3., 3.],
       [5., 5., 5., 5., 5., 5., 5., 5., 5., 5.],
       [6., 6., 6., 6., 6., 2., 2., 2., 2., 2.],
       [2., 2., 2., 2., 2., 2., 2., 2., 2., 2.],
       [4., 4., 4., 4., 4., 4., 4., 4., 4., 4.],
       [4., 4., 4., 4., 4., 4., 4., 4., 4., 4.],
       [6., 6., 6., 5., 5., 5., 5., 5., 5., 5.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       [6., 6., 6., 0., 0., 0., 0., 0., 0., 0.],
       [6., 6., 6., 6., 5., 5., 5., 5., 5., 5.]])

In [22]:
n_context_type - 1

6

In [31]:
model.fit(
        X_train, Y_train, epochs=400, batch_size=400, verbose=1,validation_data=(X_valid,Y_valid),callbacks=[ndcg_callback()])

Train on 777995 samples, validate on 178342 samples
Epoch 1/400
777995/777995 [==============================] - 46s 59us/step - loss: 0.5128 - binary_crossentropy: 0.5128 - binary_accuracy: 0.7209 - val_loss: 0.5140 - val_binary_crossentropy: 0.5140 - val_binary_accuracy: 0.7208
0.7207668412376221
Epoch 2/400
777995/777995 [==============================] - 44s 57us/step - loss: 0.5045 - binary_crossentropy: 0.5045 - binary_accuracy: 0.7269 - val_loss: 0.5105 - val_binary_crossentropy: 0.5105 - val_binary_accuracy: 0.7237
0.7236909981944802
Epoch 3/400
777995/777995 [==============================] - 53s 68us/step - loss: 0.5023 - binary_crossentropy: 0.5023 - binary_accuracy: 0.7282 - val_loss: 0.5098 - val_binary_crossentropy: 0.5098 - val_binary_accuracy: 0.7235
0.7235446501665339
Epoch 4/400
114400/777995 [===>..........................] - ETA: 33s - loss: 0.5016 - binary_crossentropy: 0.5016 - binary_accuracy: 0.7291

KeyboardInterrupt: 

In [38]:
model = skip_model_2()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

In [66]:
model.fit(
        X_train, Y_train, epochs=400, batch_size=400, verbose=1,validation_data=(X_valid,Y_valid),callbacks=[ndcg_callback()])

Train on 777995 samples, validate on 178342 samples
Epoch 1/400
777995/777995 [==============================] - 44s 57us/step - loss: 0.4975 - binary_crossentropy: 0.4975 - acc: 0.7327 - val_loss: 0.5059 - val_binary_crossentropy: 0.5059 - val_acc: 0.7274
0.7168552798726251
Epoch 2/400
777995/777995 [==============================] - 44s 57us/step - loss: 0.4972 - binary_crossentropy: 0.4972 - acc: 0.7330 - val_loss: 0.5055 - val_binary_crossentropy: 0.5055 - val_acc: 0.7279
0.7174337171553813
Epoch 3/400
126400/777995 [===>..........................] - ETA: 34s - loss: 0.4971 - binary_crossentropy: 0.4971 - acc: 0.7331

KeyboardInterrupt: 

In [43]:
Y_valid.shape

(178342, 10)

In [44]:
valid_input_data_context_id.shape

(178342, 10)

In [45]:
valid_input_data_context_id

array([[6., 2., 2., ..., 2., 2., 2.],
       [6., 6., 2., ..., 2., 2., 2.],
       [6., 6., 6., ..., 4., 4., 4.],
       ...,
       [6., 6., 6., ..., 2., 2., 2.],
       [6., 6., 6., ..., 5., 5., 5.],
       [6., 6., 6., ..., 0., 0., 0.]])

In [46]:
valid_output_data_context_id

NameError: name 'valid_output_data_context_id' is not defined

In [47]:
valid_output

array([[ 0.,  0.,  0., ...,  0.,  0.,  1.],
       [ 0.,  0.,  0., ...,  0.,  0.,  1.],
       [ 0.,  0.,  0., ...,  0.,  0.,  1.],
       ...,
       [ 0.,  0.,  0., ...,  0.,  1., -2.],
       [ 0.,  0.,  0., ..., -2., -2., -2.],
       [ 0.,  0.,  0., ...,  0.,  0.,  1.]])

In [52]:
a = valid_output[valid_output>=0]

In [53]:
a.shape

(1516154,)

In [56]:
a.shape[0]/valid_output.shape[0]/10

0.850138497942156

In [57]:
0.85*0.3892+0.15

0.48082

In [ ]:
        y_pred = self.model.predict(X_valid,batch_size=800)
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred == (Y_pred==Y_valid)
        
        Y_pred = Y_pred[valid_output>=0]
        
        print(Y_pred.shape)

        print(np.mean(Y_pred))

In [70]:
y_pred = model.predict(X_valid,batch_size=800)


#Y_pred = (Y_pred==Y_valid)

In [68]:
Y_pred

array([[False, False, False, ...,  True,  True,  True],
       [False, False, False, ...,  True,  True,  True],
       [False,  True,  True, ...,  True,  True,  True],
       ...,
       [False,  True, False, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True],
       [ True,  True, False, ...,  True,  True,  True]])

In [63]:
Y_valid

array([[1., 1., 1., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 0.],
       [1., 0., 0., ..., 0., 0., 0.],
       ...,
       [1., 0., 1., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.]])

In [69]:
np.mean(Y_pred)

0.7279115407475525

In [39]:
#y_pred = model.predict(X_valid,batch_size=800)
#y_pred = train_input[:,:,2]
Y_pred = 0*y_pred
Y_pred[y_pred>=0.5] = 1

Y_pred = train_input[:,:,2].astype(float)

Y_pred = (Y_pred==Y_valid)

#Y_pred = Y_pred[valid_output>=0]

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:8: DeprecationWarning: elementwise == comparison failed; this will raise an error in the future.
  


In [42]:
Y_pred = train_input[:,:,2].astype(float)


In [40]:
np.mean(Y_pred[:,0])

TypeError: 'int' object is not subscriptable

In [43]:
Y_pred

array([[ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 1.,  1.,  0., ...,  1.,  0.,  1.],
       [-2., -2., -2., ...,  0.,  0.,  0.],
       ...,
       [ 1.,  1.,  0., ...,  1.,  0.,  1.],
       [ 0.,  0.,  1., ...,  0.,  0.,  0.],
       [ 1.,  1.,  1., ...,  1.,  1.,  0.]])

In [34]:
#y_pred = model.predict(X_valid,batch_size=800)

Y_pred = 0*y_pred
Y_pred[y_pred>=0.5] = 1

error = 0

for i in range(valid_output.shape[0]):
    y = Y_valid[i,:]
    mask_y = valid_output[i,:]
    pred_y = Y_pred[i,:]
    pred_y = pred_y[mask_y>=0]
    y = y[mask_y>=0]
    tmp_1 = 0
    for j in range(len(y)):
        acc = np.mean(y[range(j+1)]==pred_y[range(j+1)])
        if y[j]==pred_y[j]:
            tmp_1 = tmp_1 + acc
    tmp_1 = tmp_1/len(y)
    error = error + tmp_1

print(error/(i+1))

0.6413295940958519


In [33]:
y_pred = model.predict(X_valid,batch_size=800)

#Y_pred = train_input[:,:,2].astype(float)
#Y_pred = Y_pred[:,9]
#Y_pred = np.reshape(Y_pred,(-1,1))
#Y_valid = hkl.load(data_path+'Y_valid.hkl')
#valid_output = hkl.load(data_path+'valid_output.hkl')


Y_pred = 0*y_pred
Y_pred[y_pred>=0.5] = 1

acc = 0

for i in range(valid_output.shape[0]):
    y = Y_valid[i,:]
    mask_y = valid_output[i,:]
    pred_y = Y_pred[i,:]
    #pred_y = pred_y[mask_y>0]
    #y = y[mask_y>0]
    if pred_y[0]==y[0]:
        acc = acc + 1
print(acc/(i+1))

0.7946922205649819


In [49]:
Y_pred.shape

(777995, 1)

In [104]:
y_pred = model.predict(X_valid,batch_size=800)

Y_pred = train_input[:,:,3]
Y_pred = Y_pred[:,9]
Y_pred = np.reshape(Y_pred,(-1,1))


acc = 0

for i in range(valid_output.shape[0]):
    y = Y_valid[i,:]
    mask_y = valid_output[i,:]
    pred_y = Y_pred[i,:]
    #pred_y = pred_y[mask_y>0]
    #y = y[mask_y>0]
    if pred_y[0]==y[0]:
        acc = acc + 1
print(acc/(i+1))

0.5142030480761682


In [106]:
np.mean(Y_valid[:,0])

0.5450482780276099

In [67]:
Y_valid

array([[0., 0., 0., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 1., 1., 1.],
       [1., 1., 1., ..., 1., 1., 0.],
       [0., 0., 1., ..., 0., 0., 0.]])

In [70]:
valid_output

array([[ 0.,  0.,  0., ...,  0.,  0.,  1.],
       [ 0.,  0.,  0., ...,  0.,  0.,  1.],
       [ 0.,  0.,  0., ...,  0.,  0.,  1.],
       ...,
       [ 0.,  0.,  0., ...,  0.,  1., -2.],
       [ 0.,  0.,  0., ..., -2., -2., -2.],
       [ 0.,  0.,  0., ...,  0.,  0.,  1.]])

In [71]:
valid_output.shape

(178342, 10)

In [79]:
valid_output[2,:]

array([0.55, 0.6 , 0.65, 0.7 , 0.75, 0.8 , 0.85, 0.9 , 0.95, 1.  ])

In [97]:
gc.collect()

7548

In [37]:
valid_output

array([[ 0.55      ,  0.6       ,  0.65      , ...,  0.9       ,
         0.95      ,  1.        ],
       [ 0.55      ,  0.6       ,  0.65      , ...,  0.9       ,
         0.95      ,  1.        ],
       [ 0.55      ,  0.6       ,  0.65      , ...,  0.9       ,
         0.95      ,  1.        ],
       ...,
       [ 0.55555556,  0.61111111,  0.66666667, ...,  0.94444444,
         1.        , -2.        ],
       [ 0.57142857,  0.64285714,  0.71428571, ..., -2.        ,
        -2.        , -2.        ],
       [ 0.55      ,  0.6       ,  0.65      , ...,  0.9       ,
         0.95      ,  1.        ]])

In [15]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X

#K.clear_session()

def skip_model_3(cell_size = 150):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
    rnn_layer = GRU(cell_size) (input_data_a)
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_result = concatenate([output_result, output_rnn_layer])

    output_result = Dense(512, activation='elu')(output_result)
    output_result = Dense(512, activation='elu')(output_result)
    output_result = Dropout(0.2)(output_result)

    output_result = Dense(1, activation='sigmoid')(output_result)
    
    output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model


In [41]:
#random emb

checkpoint = ModelCheckpoint('Data/skip_net_glove_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')


model = skip_model_3()
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=100, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:9: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=100, verbose=1, steps_per_epoch=3000, max_queue_size=35, validation_data=({'output_..., callbacks=[<__main__...)`
  if __name__ == '__main__':


Epoch 1/100
Skip_Data/log_5_20180906_000000000000.csv.parquet
 525/3000 [====>.........................] - ETA: 6:13 - loss: 0.5249 - binary_crossentropy: 0.5249 - binary_accuracy: 0.7160

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.116084). Check your callbacks.
  % delta_t_median)


1059/3000 [=========>....................] - ETA: 5:00 - loss: 0.5179 - binary_crossentropy: 0.5179 - binary_accuracy: 0.7211

...

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.154137). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 349s 116ms/step - loss: 0.4728 - binary_crossentropy: 0.4728 - binary_accuracy: 0.7532 - val_loss: 0.4782 - val_binary_crossentropy: 0.4782 - val_binary_accuracy: 0.7497
0.7416304676174056

Epoch 00010: val_binary_accuracy improved from 0.74734 to 0.74971, saving model to Data/skip_net_glove_best.hdf5
Epoch 11/100
1301/3000 [============>.................] - ETA: 3:20 - loss: 0.4707 - binary_crossentropy: 0.4707 - binary_accuracy: 0.7550

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.116029). Check your callbacks.
  % delta_t_median)


2784/3000 [==========================>...] - ETA: 25s - loss: 0.4697 - binary_crossentropy: 0.4697 - binary_accuracy: 0.7555

KeyboardInterrupt: 

In [20]:
#even more data
model = skip_model_3()
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=50, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [ndcg_callback(),reduceLROnPlat])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:5: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=50, verbose=1, steps_per_epoch=3000, max_queue_size=35, validation_data=({'output_..., callbacks=[<__main__...)`
  """


Epoch 1/50
Skip_Data/log_6_20180816_000000000000.csv.parquet
 558/3000 [====>.........................] - ETA: 5:56 - loss: 0.5253 - binary_crossentropy: 0.5253 - binary_accuracy: 0.7155- ETA: 5:51 - loss: 0.5254 - binary_crossentropy: 0.5254 - binary_accuracy:

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.130508). Check your callbacks.
  % delta_t_median)


 561/3000 [====>.........................] - ETA: 5:57 - loss: 0.5252 - binary_crossentropy: 0.5252 - binary_accuracy: 0.7156

...

1909/3000 [==================>...........] - ETA: 2:14 - loss: 0.4471 - binary_crossentropy: 0.4471 - binary_accuracy: 0.7713

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.202770). Check your callbacks.
  % delta_t_median)


1915/3000 [==================>...........] - ETA: 2:13 - loss: 0.4471 - binary_crossentropy: 0.4471 - binary_accuracy: 0.7713

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.110455). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 372s 124ms/step - loss: 0.4469 - binary_crossentropy: 0.4469 - binary_accuracy: 0.7713 - val_loss: 0.4544 - val_binary_crossentropy: 0.4544 - val_binary_accuracy: 0.7662
0.7587949509086808


In [12]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X

#K.clear_session()

def skip_model_4(cell_size = 200):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
    rnn_layer = GRU(cell_size) (input_data_a)
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_result = concatenate([output_result, output_rnn_layer])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result = Dense(512, activation='elu')(output_result)
    output_result = Dropout(0.1)(output_result)

    output_result = Dense(1, activation='sigmoid')(output_result)
    
    output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model


In [22]:
checkpoint = ModelCheckpoint('Data/skip_net_glove_enlarged_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')


model = skip_model_4()
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:7: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., max_queue_size=35, callbacks=[<__main__..., validation_data=({'output_..., steps_per_epoch=3000, verbose=1, epochs=300)`
  import sys


Epoch 1/300
Skip_Data/log_4_20180718_000000000000.csv.parquet
1232/3000 [===========>..................] - ETA: 4:39 - loss: 0.5096 - binary_crossentropy: 0.5096 - binary_accuracy: 0.7263

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.113897). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 485s 162ms/step - loss: 0.5023 - binary_crossentropy: 0.5023 - binary_accuracy: 0.7311 - val_loss: 0.5015 - val_binary_crossentropy: 0.5015 - val_binary_accuracy: 0.7318
0.7228243305099614

Epoch 00001: val_binary_accuracy improved from -inf to 0.73183, saving model to Data/skip_net_glove_enlarged_best.hdf5
Epoch 2/300
1653/3000 [===============>..............] - ETA: 3:30 - loss: 0.4923 - binary_crossentropy: 0.4923 - binary_accuracy: 0.7386

...

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.127959). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 445s 148ms/step - loss: 0.4366 - binary_crossentropy: 0.4366 - binary_accuracy: 0.7780 - val_loss: 0.4471 - val_binary_crossentropy: 0.4471 - val_binary_accuracy: 0.7708
0.7637931239174912

Epoch 00128: val_binary_accuracy did not improve from 0.77146
Epoch 129/300
 915/3000 [========>.....................] - ETA: 5:13 - loss: 0.4375 - binary_crossentropy: 0.4375 - binary_accuracy: 0.7776

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.122251). Check your callbacks.
  % delta_t_median)


1223/3000 [===========>..................] - ETA: 4:31 - loss: 0.4358 - binary_crossentropy: 0.4358 - binary_accuracy: 0.7785

KeyboardInterrupt: 

In [22]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X

#K.clear_session()

def skip_model_5(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
    rnn_layer = GRU(cell_size) (input_data_a)
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_result = concatenate([output_result, output_rnn_layer])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result = Dense(784, activation='elu')(output_result)
    output_result = Dropout(0.2)(output_result)

    output_result = Dense(1, activation='sigmoid')(output_result)
    
    output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model


In [23]:
checkpoint = ModelCheckpoint('Data/skip_net_glove_max_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')


model = skip_model_5()
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

NameError: name 'X_valid' is not defined

In [26]:
checkpoint = ModelCheckpoint('Data/skip_net_glove_max_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [ndcg_callback(),reduceLROnPlat,checkpoint])

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:5: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=300, steps_per_epoch=3000, validation_data=({'output_..., max_queue_size=35, callbacks=[<__main__..., verbose=1)`
  """


Epoch 1/300
Skip_Data/log_0_20180717_000000000000.csv.parquet
3000/3000 [==============================] - 656s 219ms/step - loss: 0.5019 - binary_crossentropy: 0.5019 - binary_accuracy: 0.7314 - val_loss: 0.4986 - val_binary_crossentropy: 0.4986 - val_binary_accuracy: 0.7344
0.725438181081869

Epoch 00001: val_binary_accuracy improved from -inf to 0.73442, saving model to Data/skip_net_glove_max_best.hdf5
Epoch 2/300
3000/3000 [==============================] - 614s 205ms/step - loss: 0.4883 - binary_crossentropy: 0.4883 - binary_accuracy: 0.7418 - val_loss: 0.4922 - val_binary_crossentropy: 0.4922 - val_binary_accuracy: 0.7398
0.7310002809740963

Epoch 00002: val_binary_accuracy improved from 0.73442 to 0.73976, saving model to Data/skip_net_glove_max_best.hdf5
Epoch 3/300
3000/3000 [==============================] - 602s 201ms/step - loss: 0.4823 - binary_crossentropy: 0.4823 - binary_accuracy: 0.7464 - val_loss: 0.4895 - val_binary_crossentropy: 0.4895 - val_binary_accuracy: 0.7417

3000/3000 [==============================] - 608s 203ms/step - loss: 0.4789 - binary_crossentropy: 0.4789 - binary_accuracy: 0.7488 - val_loss: 0.4837 - val_binary_crossentropy: 0.4837 - val_binary_accuracy: 0.7454
0.7369970332828987

Epoch 00004: val_binary_accuracy improved from 0.74169 to 0.74538, saving model to Data/skip_net_glove_max_best.hdf5
Epoch 5/300
3000/3000 [==============================] - 605s 202ms/step - loss: 0.4719 - binary_crossentropy: 0.4719 - binary_accuracy: 0.7535 - val_loss: 0.4763 - val_binary_crossentropy: 0.4763 - val_binary_accuracy: 0.7507
0.7427471088029316

Epoch 00005: val_binary_accuracy improved from 0.74538 to 0.75068, saving model to Data/skip_net_glove_max_best.hdf5
Epoch 6/300
3000/3000 [==============================] - 596s 199ms/step - loss: 0.4663 - binary_crossentropy: 0.4663 - binary_accuracy: 0.7576 - val_loss: 0.4720 - val_binary_crossentropy: 0.4720 - val_binary_accuracy: 0.7540
0.7463232626764827

Epoch 00006: val_binary_accuracy impr

2897/3000 [===========================>..] - ETA: 20s - loss: 0.4576 - binary_crossentropy: 0.4576 - binary_accuracy: 0.7640

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.132371). Check your callbacks.
  % delta_t_median)


...

3000/3000 [==============================] - 613s 204ms/step - loss: 0.4363 - binary_crossentropy: 0.4363 - binary_accuracy: 0.7784 - val_loss: 0.4442 - val_binary_crossentropy: 0.4442 - val_binary_accuracy: 0.7733
0.7660950009036022

Epoch 00116: val_binary_accuracy improved from 0.77328 to 0.77330, saving model to Data/skip_net_glove_max_best.hdf5
Epoch 117/300
3000/3000 [==============================] - 600s 200ms/step - loss: 0.4352 - binary_crossentropy: 0.4352 - binary_accuracy: 0.7790 - val_loss: 0.4450 - val_binary_crossentropy: 0.4450 - val_binary_accuracy: 0.7725
0.7652784611589588

Epoch 00117: val_binary_accuracy did not improve from 0.77330
Epoch 118/300
 186/3000 [>.............................] - ETA: 7:55 - loss: 0.4379 - binary_crossentropy: 0.4379 - binary_accuracy: 0.7776Skip_Data/log_7_20180906_000000000000.csv.parquet


3000/3000 [==============================] - 610s 203ms/step - loss: 0.4354 - binary_crossentropy: 0.4354 - binary_accuracy: 0.7789 - val_loss: 0.4442 - val_binary_crossentropy: 0.4442 - val_binary_accuracy: 0.7731
0.7658740470954798

Epoch 00118: val_binary_accuracy did not improve from 0.77330
Epoch 119/300
3000/3000 [==============================] - 603s 201ms/step - loss: 0.4352 - binary_crossentropy: 0.4352 - binary_accuracy: 0.7790 - val_loss: 0.4445 - val_binary_crossentropy: 0.4445 - val_binary_accuracy: 0.7728
0.7655297548929726

Epoch 00119: val_binary_accuracy did not improve from 0.77330
Epoch 120/300
3000/3000 [==============================] - 671s 224ms/step - loss: 0.4350 - binary_crossentropy: 0.4350 - binary_accuracy: 0.7792 - val_loss: 0.4446 - val_binary_crossentropy: 0.4446 - val_binary_accuracy: 0.7729
0.7656676036866967

Epoch 00120: val_binary_accuracy did not improve from 0.77330
Epoch 121/300
2199/3000 [====================>.........] - ETA: 3:11 - loss: 0.43

3000/3000 [==============================] - 725s 242ms/step - loss: 0.4356 - binary_crossentropy: 0.4356 - binary_accuracy: 0.7788 - val_loss: 0.4445 - val_binary_crossentropy: 0.4445 - val_binary_accuracy: 0.7729
0.7657632404096154

Epoch 00121: val_binary_accuracy did not improve from 0.77330
Epoch 122/300
3000/3000 [==============================] - 643s 214ms/step - loss: 0.4355 - binary_crossentropy: 0.4355 - binary_accuracy: 0.7789 - val_loss: 0.4443 - val_binary_crossentropy: 0.4443 - val_binary_accuracy: 0.7731
0.7658522814964707

Epoch 00122: val_binary_accuracy did not improve from 0.77330
Epoch 123/300
3000/3000 [==============================] - 640s 213ms/step - loss: 0.4355 - binary_crossentropy: 0.4355 - binary_accuracy: 0.7788 - val_loss: 0.4443 - val_binary_crossentropy: 0.4443 - val_binary_accuracy: 0.7732
0.7660165128344483

Epoch 00123: val_binary_accuracy did not improve from 0.77330
Epoch 124/300
3000/3000 [==============================] - 647s 216ms/step - loss

1727/3000 [================>.............] - ETA: 4:18 - loss: 0.4352 - binary_crossentropy: 0.4352 - binary_accuracy: 0.7792

KeyboardInterrupt: 

In [17]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

def skip_model_5_mtsk(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
    rnn_layer = GRU(cell_size) (input_data_a)
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_result = concatenate([output_result, output_rnn_layer])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(8, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')


model = skip_model_5_mtsk()
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:133: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=300, callbacks=[<__main__..., validation_data=({'input_f..., steps_per_epoch=3000, max_queue_size=35, verbose=1)`


Epoch 1/300
Skip_Data/log_9_20180811_000000000000.csv.parquet
3000/3000 [==============================] - 644s 215ms/step - loss: 0.3899 - binary_crossentropy: 0.3899 - binary_accuracy: 0.8166 - val_loss: 0.3829 - val_binary_crossentropy: 0.3829 - val_binary_accuracy: 0.8203
0.7282578154989533

Epoch 00001: val_binary_accuracy improved from -inf to 0.82027, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 2/300
3000/3000 [==============================] - 623s 208ms/step - loss: 0.3765 - binary_crossentropy: 0.3765 - binary_accuracy: 0.8236 - val_loss: 0.3768 - val_binary_crossentropy: 0.3768 - val_binary_accuracy: 0.8236
0.7341398037402533

Epoch 00002: val_binary_accuracy improved from 0.82027 to 0.82358, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 3/300
3000/3000 [==============================] - 616s 205ms/step - loss: 0.3724 - binary_crossentropy: 0.3724 - binary_accuracy: 0.8258 - val_loss: 0.3727 - val_binary_crossentropy: 0.3727 - val_binary_accur

3000/3000 [==============================] - 620s 207ms/step - loss: 0.3692 - binary_crossentropy: 0.3692 - binary_accuracy: 0.8276 - val_loss: 0.3694 - val_binary_crossentropy: 0.3694 - val_binary_accuracy: 0.8276
0.7422049475185238

Epoch 00004: val_binary_accuracy improved from 0.82575 to 0.82757, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 5/300
3000/3000 [==============================] - 681s 227ms/step - loss: 0.3658 - binary_crossentropy: 0.3658 - binary_accuracy: 0.8295 - val_loss: 0.3662 - val_binary_crossentropy: 0.3662 - val_binary_accuracy: 0.8296
0.7467440642573248

Epoch 00005: val_binary_accuracy improved from 0.82757 to 0.82956, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 6/300
3000/3000 [==============================] - 688s 229ms/step - loss: 0.3608 - binary_crossentropy: 0.3608 - binary_accuracy: 0.8324 - val_loss: 0.3632 - val_binary_crossentropy: 0.3632 - val_binary_accuracy: 0.8311
0.7502390918072966

Epoch 00006: val_binary_acc

3000/3000 [==============================] - 614s 205ms/step - loss: 0.3568 - binary_crossentropy: 0.3568 - binary_accuracy: 0.8347 - val_loss: 0.3593 - val_binary_crossentropy: 0.3593 - val_binary_accuracy: 0.8335
0.7546073815720566

Epoch 00008: val_binary_accuracy improved from 0.83283 to 0.83353, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 9/300
3000/3000 [==============================] - 607s 202ms/step - loss: 0.3570 - binary_crossentropy: 0.3570 - binary_accuracy: 0.8345 - val_loss: 0.3587 - val_binary_crossentropy: 0.3587 - val_binary_accuracy: 0.8337
0.7549998219178263

Epoch 00009: val_binary_accuracy improved from 0.83353 to 0.83369, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 10/300
3000/3000 [==============================] - 611s 204ms/step - loss: 0.3529 - binary_crossentropy: 0.3529 - binary_accuracy: 0.8369 - val_loss: 0.3574 - val_binary_crossentropy: 0.3574 - val_binary_accuracy: 0.8342
0.75651286083076

Epoch 00010: val_binary_accu

...

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.182870). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 611s 204ms/step - loss: 0.3423 - binary_crossentropy: 0.3423 - binary_accuracy: 0.8422 - val_loss: 0.3452 - val_binary_crossentropy: 0.3452 - val_binary_accuracy: 0.8405
0.7667750109817341

Epoch 00094: val_binary_accuracy did not improve from 0.84059
Epoch 95/300
Skip_Data/log_0_20180914_000000000000.csv.parquet
3000/3000 [==============================] - 608s 203ms/step - loss: 0.3419 - binary_crossentropy: 0.3419 - binary_accuracy: 0.8424 - val_loss: 0.3457 - val_binary_crossentropy: 0.3457 - val_binary_accuracy: 0.8403
0.7664287400884079

Epoch 00095: val_binary_accuracy did not improve from 0.84059
Epoch 96/300
3000/3000 [==============================] - 615s 205ms/step - loss: 0.3418 - binary_crossentropy: 0.3418 - binary_accuracy: 0.8425 - val_loss: 0.3456 - val_binary_crossentropy: 0.3456 - val_binary_accuracy: 0.8404
0.766654970405381

Epoch 00096: val_binary_accuracy did not improve from 0.84059
Epoch 97/300
3000/3000 [==========

3000/3000 [==============================] - 664s 221ms/step - loss: 0.3415 - binary_crossentropy: 0.3415 - binary_accuracy: 0.8426 - val_loss: 0.3451 - val_binary_crossentropy: 0.3451 - val_binary_accuracy: 0.8405
0.7671793234724177

Epoch 00098: val_binary_accuracy did not improve from 0.84059
Epoch 99/300
3000/3000 [==============================] - 634s 211ms/step - loss: 0.3419 - binary_crossentropy: 0.3419 - binary_accuracy: 0.8424 - val_loss: 0.3453 - val_binary_crossentropy: 0.3453 - val_binary_accuracy: 0.8404
0.766662885168657

Epoch 00099: ReduceLROnPlateau reducing learning rate to 0.0001.

Epoch 00099: val_binary_accuracy did not improve from 0.84059
Epoch 100/300
3000/3000 [==============================] - 616s 205ms/step - loss: 0.3407 - binary_crossentropy: 0.3407 - binary_accuracy: 0.8432 - val_loss: 0.3453 - val_binary_crossentropy: 0.3453 - val_binary_accuracy: 0.8405
0.7669669439911777

Epoch 00100: val_binary_accuracy did not improve from 0.84059
Epoch 101/300
214

3000/3000 [==============================] - 634s 211ms/step - loss: 0.3409 - binary_crossentropy: 0.3409 - binary_accuracy: 0.8430 - val_loss: 0.3452 - val_binary_crossentropy: 0.3452 - val_binary_accuracy: 0.8405
0.7669089023938201

Epoch 00101: val_binary_accuracy did not improve from 0.84059
Epoch 102/300
 183/3000 [>.............................] - ETA: 9:12 - loss: 0.3408 - binary_crossentropy: 0.3408 - binary_accuracy: 0.8430

KeyboardInterrupt: 

In [17]:
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:3: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., steps_per_epoch=3000, max_queue_size=35, callbacks=[<__main__..., validation_data=({'output_..., epochs=300, verbose=1)`
  This is separate from the ipykernel package so we can avoid doing imports until


Epoch 1/300
Skip_Data/log_1_20180802_000000000000.csv.parquet
3000/3000 [==============================] - 635s 212ms/step - loss: 0.3900 - binary_crossentropy: 0.3900 - binary_accuracy: 0.8164 - val_loss: 0.3829 - val_binary_crossentropy: 0.3829 - val_binary_accuracy: 0.8203
0.7284167703280802

Epoch 00001: val_binary_accuracy improved from -inf to 0.82031, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 2/300
3000/3000 [==============================] - 602s 201ms/step - loss: 0.3766 - binary_crossentropy: 0.3766 - binary_accuracy: 0.8235 - val_loss: 0.3771 - val_binary_crossentropy: 0.3771 - val_binary_accuracy: 0.8234
0.7344306712906472

Epoch 00002: val_binary_accuracy improved from 0.82031 to 0.82340, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 3/300
3000/3000 [==============================] - 603s 201ms/step - loss: 0.3722 - binary_crossentropy: 0.3722 - binary_accuracy: 0.8259 - val_loss: 0.3726 - val_binary_crossentropy: 0.3726 - val_binary_accur

3000/3000 [==============================] - 596s 199ms/step - loss: 0.3682 - binary_crossentropy: 0.3682 - binary_accuracy: 0.8281 - val_loss: 0.3699 - val_binary_crossentropy: 0.3699 - val_binary_accuracy: 0.8272
0.7413851099558488

Epoch 00004: val_binary_accuracy improved from 0.82560 to 0.82717, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 5/300
3000/3000 [==============================] - 604s 201ms/step - loss: 0.3658 - binary_crossentropy: 0.3658 - binary_accuracy: 0.8295 - val_loss: 0.3657 - val_binary_crossentropy: 0.3657 - val_binary_accuracy: 0.8298
0.7469755710831485

Epoch 00005: val_binary_accuracy improved from 0.82717 to 0.82976, saving model to Data/skip_net_glove_max_mtsk_best.hdf5
Epoch 6/300
3000/3000 [==============================] - 597s 199ms/step - loss: 0.3604 - binary_crossentropy: 0.3604 - binary_accuracy: 0.8327 - val_loss: 0.3631 - val_binary_crossentropy: 0.3631 - val_binary_accuracy: 0.8313
0.7501559867928983

Epoch 00006: val_binary_acc

 705/3000 [======>.......................] - ETA: 7:12 - loss: 0.3577 - binary_crossentropy: 0.3577 - binary_accuracy: 0.8342

KeyboardInterrupt: 

In [19]:
from ChainCRF import ChainCRF

# now: model.output_shape == (None, timesteps, nb_classes)

# Compile model with chain crf loss (and one-hot encoded labels) and accuracy
#model.compile(loss=crf.loss, optimizer='sgd', metrics=['accuracy'])



def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred.argmax(-1)
        
        Y_valid_i = Y_valid.argmax(-1)
                
        y_pred = (y_pred==Y_valid_i)
        
        y_pred = y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

def skip_model_5_crf(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
    rnn_layer = GRU(cell_size) (input_data_a)
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_result = concatenate([output_result, output_rnn_layer])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result = Dense(784, activation='elu')(output_result)
    output_result = Dropout(0.2)(output_result)
    
    output_result = Dense(2)(output_result)
    
    crf = ChainCRF()
    # now: model.output_shape == (None, timesteps, nb_classes)
    # Compile model with chain crf loss (and one-hot encoded labels) and accuracy
    #model.compile(loss=crf.loss, optimizer='sgd', metrics=['accuracy'])    

    
    output = crf(output_result)

    #output_result = Dense(4, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output)

    sgd = Adam(lr=0.0008)
    model.compile(loss = crf.loss, 
                  optimizer=sgd,
                  metrics = ['accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_crf_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')


model = skip_model_5_crf()
model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:144: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=300, validation_data=({'context..., steps_per_epoch=3000, verbose=1, callbacks=[<__main__..., max_queue_size=35)`


Epoch 1/300
Skip_Data/log_1_20180827_000000000000.csv.parquet
3000/3000 [==============================] - 774s 258ms/step - loss: 4.4911 - acc: 0.6123 - val_loss: 7.0814 - val_acc: 0.7237
0.7143772994036226
Epoch 2/300
3000/3000 [==============================] - 631s 210ms/step - loss: 4.3451 - acc: 0.6196 - val_loss: 6.7609 - val_acc: 0.7317
0.7233770448120705
Epoch 3/300
 443/3000 [===>..........................] - ETA: 8:56 - loss: 4.3101 - acc: 0.6229- ETA: 8:58 - loss: 4.3096 - acc: 

KeyboardInterrupt: 

In [20]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_5, rnn_layer_8])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(3*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,3*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
   # output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True))(output_rnn_layer)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(8, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_att_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])


(1, 10, 1)
(?, ?, 300)
(1, 10, 1)
(?, 10, 300)
(1, 10, 1)
(?, ?, 300)
(1, 10, 1)
(?, 10, 300)
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
_______________

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:180: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., max_queue_size=35, verbose=1, callbacks=[<__main__..., steps_per_epoch=3000, epochs=300, validation_data=({'start':...)`


Epoch 1/300
Skip_Data/log_4_20180725_000000000000.csv.parquet
3000/3000 [==============================] - 884s 295ms/step - loss: 0.3888 - binary_crossentropy: 0.3888 - binary_accuracy: 0.8171 - val_loss: 0.3816 - val_binary_crossentropy: 0.3816 - val_binary_accuracy: 0.8211
0.7301177848688194

Epoch 00001: val_binary_accuracy improved from -inf to 0.82106, saving model to Data/skip_net_glove_max_mtsk_att_best.hdf5
Epoch 2/300
3000/3000 [==============================] - 865s 288ms/step - loss: 0.3762 - binary_crossentropy: 0.3762 - binary_accuracy: 0.8236 - val_loss: 0.3766 - val_binary_crossentropy: 0.3766 - val_binary_accuracy: 0.8235
0.7346918584787561

Epoch 00002: val_binary_accuracy improved from 0.82106 to 0.82354, saving model to Data/skip_net_glove_max_mtsk_att_best.hdf5
Epoch 3/300
3000/3000 [==============================] - 850s 283ms/step - loss: 0.3719 - binary_crossentropy: 0.3719 - binary_accuracy: 0.8261 - val_loss: 0.3729 - val_binary_crossentropy: 0.3729 - val_bina

KeyboardInterrupt: 

In [ ]:
'''
def skip_model_5_mtsk_att(cell_size = 20):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    rnn_layer_last = Lambda(slice_last)(input_data_a)      
#    print(encoder_outputs.shape)
    print(rnn_layer.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_last])
    
    print(rnn_layer.shape)
    
    # output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data_i, emb_output_id])

    output_data = Dense(spotify_song_array.shape[1]+input_fea_dim+cell_size+60, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,spotify_song_array.shape[1]+input_fea_dim+cell_size+60])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_result = concatenate([output_result, output_rnn_layer])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(8, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_lgb_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

K.clear_session()

model = skip_model_5_mtsk_att()


In [14]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    #rnn_layer = concatenate([rnn_layer, rnn_layer_5, rnn_layer_8])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True))(output_rnn_layer)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(8, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_2layer_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:182: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=300, verbose=1, max_queue_size=35, callbacks=[<__main__..., validation_data=({'output_..., steps_per_epoch=3000)`


Epoch 1/300
Skip_Data/log_3_20180729_000000000000.csv.parquet
3000/3000 [==============================] - 833s 278ms/step - loss: 0.3886 - binary_crossentropy: 0.3886 - binary_accuracy: 0.8172 - val_loss: 0.3797 - val_binary_crossentropy: 0.3797 - val_binary_accuracy: 0.8220
0.7315371657496534

Epoch 00001: val_binary_accuracy improved from -inf to 0.82201, saving model to Data/skip_net_glove_max_mtsk_2layer_best.hdf5
Epoch 2/300
3000/3000 [==============================] - 905s 302ms/step - loss: 0.3699 - binary_crossentropy: 0.3699 - binary_accuracy: 0.8273 - val_loss: 0.3656 - val_binary_crossentropy: 0.3656 - val_binary_accuracy: 0.8300
0.7484424405436387

Epoch 00002: val_binary_accuracy improved from 0.82201 to 0.82996, saving model to Data/skip_net_glove_max_mtsk_2layer_best.hdf5
Epoch 3/300
  25/3000 [..............................] - ETA: 9:10 - loss: 0.3602 - binary_crossentropy: 0.3602 - binary_accuracy: 0.8334

KeyboardInterrupt: 

In [25]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    encoder_outputs_1, rnn_layer_1 = GRU(cell_size, return_sequences=True, return_state=True) (encoder_outputs)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_1])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(2*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,2*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True),merge_mode='ave')(output_rnn_layer)
    
    output_rnn_layer_3 = Bidirectional(GRU(100, return_sequences=True),merge_mode='ave')(output_rnn_layer_2)
    
    output_rnn_layer_4 = Bidirectional(GRU(100, return_sequences=True),merge_mode='ave')(output_rnn_layer_3)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2, output_rnn_layer_3, output_rnn_layer_4])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(8, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_more_layer_best.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:188: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., steps_per_epoch=3000, callbacks=[<__main__..., verbose=1, max_queue_size=35, validation_data=({'end': a..., epochs=300)`


Epoch 1/300
Skip_Data/log_8_20180815_000000000000.csv.parquet
3000/3000 [==============================] - 1129s 376ms/step - loss: 0.3870 - binary_crossentropy: 0.3870 - binary_accuracy: 0.8180 - val_loss: 0.3778 - val_binary_crossentropy: 0.3778 - val_binary_accuracy: 0.8228
0.7333700930116598

Epoch 00001: val_binary_accuracy improved from -inf to 0.82283, saving model to Data/skip_net_glove_max_mtsk_more_layer_best.hdf5
Epoch 2/300
3000/3000 [==============================] - 1100s 367ms/step - loss: 0.3639 - binary_crossentropy: 0.3639 - binary_accuracy: 0.8309 - val_loss: 0.3618 - val_binary_crossentropy: 0.3618 - val_binary_accuracy: 0.8324
0.7533225516669151

Epoch 00002: val_binary_accuracy improved from 0.82283 to 0.83236, saving model to Data/skip_net_glove_max_mtsk_more_layer_best.hdf5
Epoch 3/300
3000/3000 [==============================] - 1103s 368ms/step - loss: 0.3564 - binary_crossentropy: 0.3564 - binary_accuracy: 0.8351 - val_loss: 0.3587 - val_binary_crossentropy: 

3000/3000 [==============================] - 1106s 369ms/step - loss: 0.3556 - binary_crossentropy: 0.3556 - binary_accuracy: 0.8353 - val_loss: 0.3573 - val_binary_crossentropy: 0.3573 - val_binary_accuracy: 0.8344
0.7566282844618687

Epoch 00004: val_binary_accuracy improved from 0.83385 to 0.83436, saving model to Data/skip_net_glove_max_mtsk_more_layer_best.hdf5
Epoch 5/300
3000/3000 [==============================] - 1103s 368ms/step - loss: 0.3518 - binary_crossentropy: 0.3518 - binary_accuracy: 0.8373 - val_loss: 0.3556 - val_binary_crossentropy: 0.3556 - val_binary_accuracy: 0.8352
0.7580839413410511

Epoch 00005: val_binary_accuracy improved from 0.83436 to 0.83524, saving model to Data/skip_net_glove_max_mtsk_more_layer_best.hdf5
Epoch 6/300
3000/3000 [==============================] - 1102s 367ms/step - loss: 0.3513 - binary_crossentropy: 0.3513 - binary_accuracy: 0.8376 - val_loss: 0.3537 - val_binary_crossentropy: 0.3537 - val_binary_accuracy: 0.8362
0.7598238701345642

Ep

3000/3000 [==============================] - 1215s 405ms/step - loss: 0.3482 - binary_crossentropy: 0.3482 - binary_accuracy: 0.8392 - val_loss: 0.3529 - val_binary_crossentropy: 0.3529 - val_binary_accuracy: 0.8368
0.7601681623370713

Epoch 00008: val_binary_accuracy improved from 0.83649 to 0.83675, saving model to Data/skip_net_glove_max_mtsk_more_layer_best.hdf5
Epoch 9/300
3000/3000 [==============================] - 1259s 420ms/step - loss: 0.3484 - binary_crossentropy: 0.3484 - binary_accuracy: 0.8390 - val_loss: 0.3525 - val_binary_crossentropy: 0.3525 - val_binary_accuracy: 0.8368
0.7609576599738549

Epoch 00009: val_binary_accuracy improved from 0.83675 to 0.83679, saving model to Data/skip_net_glove_max_mtsk_more_layer_best.hdf5
Epoch 10/300
3000/3000 [==============================] - 1310s 437ms/step - loss: 0.3484 - binary_crossentropy: 0.3484 - binary_accuracy: 0.8391 - val_loss: 0.3519 - val_binary_crossentropy: 0.3519 - val_binary_accuracy: 0.8370
0.7604194560710851

E

...

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.301037). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 1224s 408ms/step - loss: 0.3368 - binary_crossentropy: 0.3368 - binary_accuracy: 0.8450 - val_loss: 0.3410 - val_binary_crossentropy: 0.3410 - val_binary_accuracy: 0.8427
0.7701183389022487

Epoch 00188: val_binary_accuracy did not improve from 0.84288
Epoch 189/300
2661/3000 [=========================>....] - ETA: 2:14 - loss: 0.3359 - binary_crossentropy: 0.3359 - binary_accuracy: 0.8455Skip_Data/log_0_20180826_000000000000.csv.parquet


3000/3000 [==============================] - 1195s 398ms/step - loss: 0.3359 - binary_crossentropy: 0.3359 - binary_accuracy: 0.8456 - val_loss: 0.3408 - val_binary_crossentropy: 0.3408 - val_binary_accuracy: 0.8427
0.7704606524139368

Epoch 00189: val_binary_accuracy did not improve from 0.84288
Epoch 190/300
3000/3000 [==============================] - 1183s 394ms/step - loss: 0.3362 - binary_crossentropy: 0.3362 - binary_accuracy: 0.8454 - val_loss: 0.3410 - val_binary_crossentropy: 0.3410 - val_binary_accuracy: 0.8426
0.7702265073336877

Epoch 00190: val_binary_accuracy did not improve from 0.84288
Epoch 191/300
3000/3000 [==============================] - 1242s 414ms/step - loss: 0.3361 - binary_crossentropy: 0.3361 - binary_accuracy: 0.8454 - val_loss: 0.3411 - val_binary_crossentropy: 0.3411 - val_binary_accuracy: 0.8427
0.7705371617922717

Epoch 00191: val_binary_accuracy did not improve from 0.84288
Epoch 192/300
3000/3000 [==============================] - 1199s 400ms/step - 

3000/3000 [==============================] - 1210s 403ms/step - loss: 0.3345 - binary_crossentropy: 0.3345 - binary_accuracy: 0.8463 - val_loss: 0.3412 - val_binary_crossentropy: 0.3412 - val_binary_accuracy: 0.8426
0.7702027630438597

Epoch 00193: val_binary_accuracy did not improve from 0.84288
Epoch 194/300
 595/3000 [====>.........................] - ETA: 15:20 - loss: 0.3379 - binary_crossentropy: 0.3379 - binary_accuracy: 0.8443

KeyboardInterrupt: 

In [20]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    encoder_outputs_1, rnn_layer_1 = GRU(cell_size, return_sequences=True, return_state=True) (encoder_outputs)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_1])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(2*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,2*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True),merge_mode='ave')(output_rnn_layer)
    
    output_rnn_layer_3 = Bidirectional(GRU(100, return_sequences=True),merge_mode='ave')(output_rnn_layer_2)
    
    output_rnn_layer_4 = Bidirectional(GRU(100, return_sequences=True),merge_mode='ave')(output_rnn_layer_3)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2, output_rnn_layer_3, output_rnn_layer_4])

    output_result = Dense(1024, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(8, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_more_layer_best_v2.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:188: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., steps_per_epoch=3000, max_queue_size=35, verbose=1, callbacks=[<__main__..., validation_data=({'end': a..., epochs=300)`


Epoch 1/300
3000/3000 [==============================] - 1890s 630ms/step - loss: 0.3835 - binary_crossentropy: 0.3835 - binary_accuracy: 0.8200 - val_loss: 0.3706 - val_binary_crossentropy: 0.3706 - val_binary_accuracy: 0.8270
0.7425268145584155

Epoch 00001: val_binary_accuracy improved from -inf to 0.82702, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v2.hdf5
Epoch 2/300
3000/3000 [==============================] - 1901s 634ms/step - loss: 0.3595 - binary_crossentropy: 0.3595 - binary_accuracy: 0.8333 - val_loss: 0.3587 - val_binary_crossentropy: 0.3587 - val_binary_accuracy: 0.8337
0.75544370822489

Epoch 00002: val_binary_accuracy improved from 0.82702 to 0.83375, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v2.hdf5
Epoch 3/300
3000/3000 [==============================] - 1859s 620ms/step - loss: 0.3539 - binary_crossentropy: 0.3539 - binary_accuracy: 0.8363 - val_loss: 0.3555 - val_binary_crossentropy: 0.3555 - val_binary_accuracy: 0.8354
0.7582659

0.7687695313272926

Epoch 00046: val_binary_accuracy did not improve from 0.84200
Epoch 47/300
3000/3000 [==============================] - 1905s 635ms/step - loss: 0.3388 - binary_crossentropy: 0.3388 - binary_accuracy: 0.8440 - val_loss: 0.3422 - val_binary_crossentropy: 0.3422 - val_binary_accuracy: 0.8420
0.7686514694417586

Epoch 00047: val_binary_accuracy improved from 0.84200 to 0.84202, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v2.hdf5
Epoch 48/300
3000/3000 [==============================] - 1936s 645ms/step - loss: 0.3381 - binary_crossentropy: 0.3381 - binary_accuracy: 0.8444 - val_loss: 0.3429 - val_binary_crossentropy: 0.3429 - val_binary_accuracy: 0.8417
0.7681257972475092

Epoch 00048: val_binary_accuracy did not improve from 0.84202
Epoch 49/300
3000/3000 [==============================] - 1925s 642ms/step - loss: 0.3383 - binary_crossentropy: 0.3383 - binary_accuracy: 0.8442 - val_loss: 0.3419 - val_binary_crossentropy: 0.3419 - val_binary_accuracy: 

Epoch 71/300
3000/3000 [==============================] - 1938s 646ms/step - loss: 0.3363 - binary_crossentropy: 0.3363 - binary_accuracy: 0.8453 - val_loss: 0.3410 - val_binary_crossentropy: 0.3410 - val_binary_accuracy: 0.8426
0.7699343206560811

Epoch 00071: val_binary_accuracy did not improve from 0.84265
Epoch 72/300
3000/3000 [==============================] - 1941s 647ms/step - loss: 0.3362 - binary_crossentropy: 0.3362 - binary_accuracy: 0.8454 - val_loss: 0.3406 - val_binary_crossentropy: 0.3406 - val_binary_accuracy: 0.8429
0.7702331029697511

Epoch 00072: val_binary_accuracy improved from 0.84265 to 0.84291, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v2.hdf5
Epoch 73/300
3000/3000 [==============================] - 1954s 651ms/step - loss: 0.3364 - binary_crossentropy: 0.3364 - binary_accuracy: 0.8453 - val_loss: 0.3412 - val_binary_crossentropy: 0.3412 - val_binary_accuracy: 0.8425
0.7699369589105064

Epoch 00073: val_binary_accuracy did not improve from 0

KeyboardInterrupt: 

In [13]:
batch_size

3000

In [21]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att_bn(cell_size = 300):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    encoder_outputs_1, rnn_layer_1 = GRU(cell_size, return_sequences=True, return_state=True) (encoder_outputs)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_1])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(2*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,2*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True),merge_mode='ave')(output_rnn_layer)
    
    output_rnn_layer_3 = Bidirectional(GRU(100, return_sequences=True),merge_mode='ave')(output_rnn_layer_2)
    
    output_rnn_layer_4 = Bidirectional(GRU(100, return_sequences=True),merge_mode='ave')(output_rnn_layer_3)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2, output_rnn_layer_3, output_rnn_layer_4])
    
    #output_result = Reshape([2900*10])(output_result)     
    output_result = BatchNormalization()(output_result)
    #output_result = Reshape([10,2900])(output_result)     

    output_result = Dense(1024)(output_result)
    output_result = BatchNormalization()(output_result)
    output_result = Activation(activation='elu')(output_result)
        
    output_result_1 = Dense(784)(output_result)
    output_result_1 = BatchNormalization()(output_result_1)
    output_result_1 = Activation(activation='elu')(output_result_1)    
    
    output_result_2 = Dropout(0.2)(output_result_1)

    output_result_2 = Dense(8, activation='sigmoid')(output_result_2)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result_2)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_more_layer_best_bn.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att_bn()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:194: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., max_queue_size=35, steps_per_epoch=3000, epochs=300, verbose=1, validation_data=({'end': a..., callbacks=[<__main__...)`


Epoch 1/300
3000/3000 [==============================] - 2082s 694ms/step - loss: 0.3847 - binary_crossentropy: 0.3847 - binary_accuracy: 0.8196 - val_loss: 0.3682 - val_binary_crossentropy: 0.3682 - val_binary_accuracy: 0.8290
0.7476476663980044

Epoch 00001: val_binary_accuracy improved from -inf to 0.82902, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_bn.hdf5
Epoch 2/300
3000/3000 [==============================] - 2052s 684ms/step - loss: 0.3581 - binary_crossentropy: 0.3581 - binary_accuracy: 0.8342 - val_loss: 0.3581 - val_binary_crossentropy: 0.3581 - val_binary_accuracy: 0.8340
0.7557418309749537

Epoch 00002: val_binary_accuracy improved from 0.82902 to 0.83401, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_bn.hdf5
Epoch 3/300
3000/3000 [==============================] - 2001s 667ms/step - loss: 0.3526 - binary_crossentropy: 0.3526 - binary_accuracy: 0.8370 - val_loss: 0.3552 - val_binary_crossentropy: 0.3552 - val_binary_accuracy: 0.8355
0.75855

Epoch 23/300
3000/3000 [==============================] - 2174s 725ms/step - loss: 0.3417 - binary_crossentropy: 0.3417 - binary_accuracy: 0.8425 - val_loss: 0.3458 - val_binary_crossentropy: 0.3458 - val_binary_accuracy: 0.8402
0.766169531591118

Epoch 00023: val_binary_accuracy did not improve from 0.84045
Epoch 24/300
3000/3000 [==============================] - 2131s 710ms/step - loss: 0.3424 - binary_crossentropy: 0.3424 - binary_accuracy: 0.8420 - val_loss: 0.3455 - val_binary_crossentropy: 0.3455 - val_binary_accuracy: 0.8402
0.7659327482564436

Epoch 00024: val_binary_accuracy did not improve from 0.84045
Epoch 25/300
3000/3000 [==============================] - 2151s 717ms/step - loss: 0.3415 - binary_crossentropy: 0.3415 - binary_accuracy: 0.8426 - val_loss: 0.3458 - val_binary_crossentropy: 0.3458 - val_binary_accuracy: 0.8401
0.7661912971901271

Epoch 00025: val_binary_accuracy did not improve from 0.84045
Epoch 26/300
3000/3000 [==============================] - 2150s 717m

0.7676825705040518

Epoch 00046: ReduceLROnPlateau reducing learning rate to 0.00032000001519918444.

Epoch 00046: val_binary_accuracy did not improve from 0.84146
Epoch 47/300
3000/3000 [==============================] - 2160s 720ms/step - loss: 0.3397 - binary_crossentropy: 0.3397 - binary_accuracy: 0.8435 - val_loss: 0.3434 - val_binary_crossentropy: 0.3434 - val_binary_accuracy: 0.8414
0.7677115913027305

Epoch 00047: val_binary_accuracy did not improve from 0.84146
Epoch 48/300
3000/3000 [==============================] - 2158s 719ms/step - loss: 0.3399 - binary_crossentropy: 0.3399 - binary_accuracy: 0.8433 - val_loss: 0.3426 - val_binary_crossentropy: 0.3426 - val_binary_accuracy: 0.8418
0.7685604496640842

Epoch 00048: val_binary_accuracy improved from 0.84146 to 0.84180, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_bn.hdf5
Epoch 49/300
3000/3000 [==============================] - 2145s 715ms/step - loss: 0.3387 - binary_crossentropy: 0.3387 - binary_accuracy: 0

3000/3000 [==============================] - 2031s 677ms/step - loss: 0.3365 - binary_crossentropy: 0.3365 - binary_accuracy: 0.8452 - val_loss: 0.3411 - val_binary_crossentropy: 0.3411 - val_binary_accuracy: 0.8427
0.7699013424757644

Epoch 00095: ReduceLROnPlateau reducing learning rate to 0.0001310720108449459.

Epoch 00095: val_binary_accuracy did not improve from 0.84286
Epoch 96/300
3000/3000 [==============================] - 2053s 684ms/step - loss: 0.3360 - binary_crossentropy: 0.3360 - binary_accuracy: 0.8455 - val_loss: 0.3412 - val_binary_crossentropy: 0.3412 - val_binary_accuracy: 0.8426
0.7698597899685652

Epoch 00096: val_binary_accuracy did not improve from 0.84286
Epoch 97/300
3000/3000 [==============================] - 2013s 671ms/step - loss: 0.3365 - binary_crossentropy: 0.3365 - binary_accuracy: 0.8451 - val_loss: 0.3414 - val_binary_crossentropy: 0.3414 - val_binary_accuracy: 0.8425
0.7696599421958455

Epoch 00097: val_binary_accuracy did not improve from 0.84286

3000/3000 [==============================] - 2083s 694ms/step - loss: 0.3353 - binary_crossentropy: 0.3353 - binary_accuracy: 0.8458 - val_loss: 0.3408 - val_binary_crossentropy: 0.3408 - val_binary_accuracy: 0.8427
0.7698525347688955

Epoch 00146: val_binary_accuracy did not improve from 0.84287
Epoch 147/300
3000/3000 [==============================] - 2036s 679ms/step - loss: 0.3354 - binary_crossentropy: 0.3354 - binary_accuracy: 0.8458 - val_loss: 0.3409 - val_binary_crossentropy: 0.3409 - val_binary_accuracy: 0.8427
0.7698703429862666

Epoch 00147: val_binary_accuracy did not improve from 0.84287
Epoch 148/300
3000/3000 [==============================] - 2043s 681ms/step - loss: 0.3350 - binary_crossentropy: 0.3350 - binary_accuracy: 0.8460 - val_loss: 0.3407 - val_binary_crossentropy: 0.3407 - val_binary_accuracy: 0.8427
0.7699976387622893

Epoch 00148: val_binary_accuracy did not improve from 0.84287
Epoch 149/300
3000/3000 [==============================] - 2026s 675ms/step - 

KeyboardInterrupt: 

In [16]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 350):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    encoder_outputs_1, rnn_layer_1 = GRU(cell_size, return_sequences=True, return_state=True) (encoder_outputs)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_1])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(2*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,2*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True),merge_mode='ave')(output_rnn_layer)
    
    output_rnn_layer_3 = Bidirectional(GRU(200, return_sequences=True),merge_mode='ave')(output_rnn_layer_2)
    
    output_rnn_layer_4 = Bidirectional(GRU(200, return_sequences=True),merge_mode='ave')(output_rnn_layer_3)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2, output_rnn_layer_3, output_rnn_layer_4])

    output_result = Dense(1300, activation='elu')(output_result)
    output_result_1 = Dense(784, activation='elu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(11, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_more_layer_best_v3.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:188: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., verbose=1, max_queue_size=35, epochs=300, validation_data=({'context..., steps_per_epoch=3000, callbacks=[<__main__...)`


Epoch 1/300
3000/3000 [==============================] - 1723s 574ms/step - loss: 0.3006 - binary_crossentropy: 0.3006 - binary_accuracy: 0.8632 - val_loss: 0.2862 - val_binary_crossentropy: 0.2862 - val_binary_accuracy: 0.8704
0.7464505584525055

Epoch 00001: val_binary_accuracy improved from -inf to 0.87039, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v3.hdf5
Epoch 2/300
3000/3000 [==============================] - 1708s 569ms/step - loss: 0.2788 - binary_crossentropy: 0.2788 - binary_accuracy: 0.8741 - val_loss: 0.2785 - val_binary_crossentropy: 0.2785 - val_binary_accuracy: 0.8740
0.7554562399334105

Epoch 00002: val_binary_accuracy improved from 0.87039 to 0.87397, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v3.hdf5
Epoch 3/300
3000/3000 [==============================] - 1747s 582ms/step - loss: 0.2746 - binary_crossentropy: 0.2746 - binary_accuracy: 0.8760 - val_loss: 0.2760 - val_binary_crossentropy: 0.2760 - val_binary_accuracy: 0.8752
0.75774

3000/3000 [==============================] - 1738s 579ms/step - loss: 0.2615 - binary_crossentropy: 0.2615 - binary_accuracy: 0.8821 - val_loss: 0.2639 - val_binary_crossentropy: 0.2639 - val_binary_accuracy: 0.8806
0.7679147368934818

Epoch 00046: val_binary_accuracy did not improve from 0.88089
Epoch 47/300
3000/3000 [==============================] - 1744s 581ms/step - loss: 0.2610 - binary_crossentropy: 0.2610 - binary_accuracy: 0.8824 - val_loss: 0.2638 - val_binary_crossentropy: 0.2638 - val_binary_accuracy: 0.8807
0.768408750034627

Epoch 00047: val_binary_accuracy did not improve from 0.88089
Epoch 48/300
3000/3000 [==============================] - 1775s 592ms/step - loss: 0.2613 - binary_crossentropy: 0.2613 - binary_accuracy: 0.8822 - val_loss: 0.2633 - val_binary_crossentropy: 0.2633 - val_binary_accuracy: 0.8809
0.7689733364816502

Epoch 00048: val_binary_accuracy improved from 0.88089 to 0.88095, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v3.hdf5
Epoch 4

3000/3000 [==============================] - 1744s 581ms/step - loss: 0.2597 - binary_crossentropy: 0.2597 - binary_accuracy: 0.8829 - val_loss: 0.2622 - val_binary_crossentropy: 0.2622 - val_binary_accuracy: 0.8815
0.7698558325869271

Epoch 00070: val_binary_accuracy did not improve from 0.88160
Epoch 71/300
3000/3000 [==============================] - 1717s 572ms/step - loss: 0.2590 - binary_crossentropy: 0.2590 - binary_accuracy: 0.8833 - val_loss: 0.2622 - val_binary_crossentropy: 0.2622 - val_binary_accuracy: 0.8814
0.7695491355099812

Epoch 00071: val_binary_accuracy did not improve from 0.88160
Epoch 72/300
3000/3000 [==============================] - 1750s 583ms/step - loss: 0.2595 - binary_crossentropy: 0.2595 - binary_accuracy: 0.8831 - val_loss: 0.2618 - val_binary_crossentropy: 0.2618 - val_binary_accuracy: 0.8816
0.7702608046412172

Epoch 00072: val_binary_accuracy improved from 0.88160 to 0.88162, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v3.hdf5
Epoch 

KeyboardInterrupt: 

In [17]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 350):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,20)
    reason_start_emb_layer = Embedding(n_reason_start,20)
    reason_end_emb_layer = Embedding(n_reason_end,20)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    encoder_outputs_1, rnn_layer_1 = GRU(cell_size, return_sequences=True, return_state=True) (encoder_outputs)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_1])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(2*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,2*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True))(output_rnn_layer)
    
    output_rnn_layer_3 = Bidirectional(GRU(200, return_sequences=True))(output_rnn_layer_2)
    
    output_rnn_layer_4 = Bidirectional(GRU(200, return_sequences=True))(output_rnn_layer_3)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2, output_rnn_layer_3, output_rnn_layer_4])

    output_result = Dense(900, activation='relu')(output_result)
    output_result_1 = Dense(784, activation='relu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(11, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0005)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:188: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=300, steps_per_epoch=3000, callbacks=[<__main__..., max_queue_size=35, validation_data=({'start':..., verbose=1)`


Epoch 1/300
shrinkage: 3194663 3023462
3000/3000 [==============================] - 1730s 577ms/step - loss: 0.2817 - binary_crossentropy: 0.2817 - binary_accuracy: 0.8719 - val_loss: 0.2840 - val_binary_crossentropy: 0.2840 - val_binary_accuracy: 0.8712
0.7489338154303586

Epoch 00001: val_binary_accuracy improved from -inf to 0.87118, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 2/300
1297/3000 [===========>..................] - ETA: 16:31 - loss: 0.2650 - binary_crossentropy: 0.2650 - binary_accuracy: 0.8802shrinkage: 2823685 2671295


3000/3000 [==============================] - 1747s 582ms/step - loss: 0.2634 - binary_crossentropy: 0.2634 - binary_accuracy: 0.8810 - val_loss: 0.2774 - val_binary_crossentropy: 0.2774 - val_binary_accuracy: 0.8742
0.7558480207155738

Epoch 00002: val_binary_accuracy improved from 0.87118 to 0.87419, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 3/300
3000/3000 [==============================] - 1755s 585ms/step - loss: 0.2596 - binary_crossentropy: 0.2596 - binary_accuracy: 0.8827 - val_loss: 0.2750 - val_binary_crossentropy: 0.2750 - val_binary_accuracy: 0.8753
0.7580034745810782

Epoch 00003: val_binary_accuracy improved from 0.87419 to 0.87531, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 4/300
3000/3000 [==============================] - 1782s 594ms/step - loss: 0.2571 - binary_crossentropy: 0.2571 - binary_accuracy: 0.8838 - val_loss: 0.2732 - val_binary_crossentropy: 0.2732 - val_binary_accuracy: 0.8762
0.75967480875953

3000/3000 [==============================] - 1766s 589ms/step - loss: 0.2559 - binary_crossentropy: 0.2559 - binary_accuracy: 0.8844 - val_loss: 0.2721 - val_binary_crossentropy: 0.2721 - val_binary_accuracy: 0.8767
0.7607307700932755

Epoch 00005: val_binary_accuracy improved from 0.87625 to 0.87673, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 6/300
3000/3000 [==============================] - 1800s 600ms/step - loss: 0.2555 - binary_crossentropy: 0.2555 - binary_accuracy: 0.8845 - val_loss: 0.2708 - val_binary_crossentropy: 0.2708 - val_binary_accuracy: 0.8773
0.7618025609535707

Epoch 00006: val_binary_accuracy improved from 0.87673 to 0.87728, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 7/300
3000/3000 [==============================] - 1779s 593ms/step - loss: 0.2541 - binary_crossentropy: 0.2541 - binary_accuracy: 0.8853 - val_loss: 0.2704 - val_binary_crossentropy: 0.2704 - val_binary_accuracy: 0.8775
0.76220753300786

...

3000/3000 [==============================] - 1792s 597ms/step - loss: 0.2454 - binary_crossentropy: 0.2454 - binary_accuracy: 0.8894 - val_loss: 0.2616 - val_binary_crossentropy: 0.2616 - val_binary_accuracy: 0.8817
0.7707000740030366

Epoch 00085: val_binary_accuracy improved from 0.88169 to 0.88175, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 86/300
3000/3000 [==============================] - 1802s 601ms/step - loss: 0.2457 - binary_crossentropy: 0.2457 - binary_accuracy: 0.8893 - val_loss: 0.2618 - val_binary_crossentropy: 0.2618 - val_binary_accuracy: 0.8816
0.7704349294332897

Epoch 00086: val_binary_accuracy did not improve from 0.88175
Epoch 87/300
3000/3000 [==============================] - 1794s 598ms/step - loss: 0.2461 - binary_crossentropy: 0.2461 - binary_accuracy: 0.8890 - val_loss: 0.2617 - val_binary_crossentropy: 0.2617 - val_binary_accuracy: 0.8817
0.770624224188308

Epoch 00087: val_binary_accuracy did not improve from 0.88175
Epoch 8

3000/3000 [==============================] - 1775s 592ms/step - loss: 0.2459 - binary_crossentropy: 0.2459 - binary_accuracy: 0.8892 - val_loss: 0.2612 - val_binary_crossentropy: 0.2612 - val_binary_accuracy: 0.8818
0.7708385823603671

Epoch 00088: val_binary_accuracy improved from 0.88175 to 0.88183, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 89/300
3000/3000 [==============================] - 1776s 592ms/step - loss: 0.2454 - binary_crossentropy: 0.2454 - binary_accuracy: 0.8894 - val_loss: 0.2611 - val_binary_crossentropy: 0.2611 - val_binary_accuracy: 0.8820
0.7708293484698784

Epoch 00089: val_binary_accuracy improved from 0.88183 to 0.88197, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v4.hdf5
Epoch 90/300
2932/3000 [============================>.] - ETA: 40s - loss: 0.2458 - binary_crossentropy: 0.2458 - binary_accuracy: 0.8892shrinkage: 3196971 3022516


3000/3000 [==============================] - 1791s 597ms/step - loss: 0.2459 - binary_crossentropy: 0.2459 - binary_accuracy: 0.8892 - val_loss: 0.2617 - val_binary_crossentropy: 0.2617 - val_binary_accuracy: 0.8817
0.7704573545959051

Epoch 00090: val_binary_accuracy did not improve from 0.88197
Epoch 91/300
3000/3000 [==============================] - 1848s 616ms/step - loss: 0.2458 - binary_crossentropy: 0.2458 - binary_accuracy: 0.8892 - val_loss: 0.2618 - val_binary_crossentropy: 0.2618 - val_binary_accuracy: 0.8816
0.7704500993962354

Epoch 00091: val_binary_accuracy did not improve from 0.88197
Epoch 92/300
3000/3000 [==============================] - 1792s 597ms/step - loss: 0.2451 - binary_crossentropy: 0.2451 - binary_accuracy: 0.8896 - val_loss: 0.2613 - val_binary_crossentropy: 0.2613 - val_binary_accuracy: 0.8818
0.7706433515328918

Epoch 00092: val_binary_accuracy did not improve from 0.88197
Epoch 93/300
2476/3000 [=======================>......] - ETA: 5:09 - loss: 0.24

3000/3000 [==============================] - 1805s 602ms/step - loss: 0.2447 - binary_crossentropy: 0.2447 - binary_accuracy: 0.8899 - val_loss: 0.2617 - val_binary_crossentropy: 0.2617 - val_binary_accuracy: 0.8817
0.7704283337972264

Epoch 00093: ReduceLROnPlateau reducing learning rate to 0.00010485760867595673.

Epoch 00093: val_binary_accuracy did not improve from 0.88197
Epoch 94/300
 937/3000 [========>.....................] - ETA: 19:45 - loss: 0.2461 - binary_crossentropy: 0.2461 - binary_accuracy: 0.8889

KeyboardInterrupt: 

In [19]:

def tile_tile(X):
    X = K.tile(X, [1,10,1]) 
    return X


def exp_smooth5(X):   
    weight = np.power(0.5,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result

def exp_smooth8(X):   
    weight = np.power(0.8,9 - np.arange(10))
    weight = weight/np.sum(weight)
    weight = np.reshape(weight, (1,10,1))
    att_output_weight = K.variable(weight)
    print(att_output_weight.shape)
    att_output_result = X*att_output_weight    
    print(X.shape)
    att_output_result = K.mean(att_output_result, axis=1)
    
    return att_output_result


class mstk_ndcg_callback(Callback):
    def __init__(self):
        return

    def on_train_begin(self, logs={}):
        return

    def on_train_end(self, logs={}):
        return

    def on_epoch_begin(self, epoch, logs={}):
        return

    def on_epoch_end(self, epoch, logs={}):      

        y_pred = self.model.predict(X_valid,batch_size=800)
        
        hkl.dump(y_pred, data_path+'y_pred.hkl', mode='w', compression='gzip')
        
        y_pred = y_pred[:,:,1]
        
        Y_valid_i = Y_valid[:,:,1]
        
        Y_pred = 0*y_pred
        Y_pred[y_pred>=0.5] = 1
        
        Y_pred = (Y_pred==Y_valid_i)
        
        Y_pred = Y_pred[valid_output>=0]
        
        #print(Y_pred.shape)

        print(np.mean(Y_pred))
        
        #hkl.dump(song_embedding_matrix, data_path+'song_embedding_matrix_80.hkl', mode='w', compression='gzip')

        return

    def on_batch_begin(self, batch, logs={}):
        return

    def on_batch_end(self, batch, logs={}):
        return

#K.clear_session()

#spotify_song_array = np.ones((100,2))
#input_fea_dim = 5
#n_context_type = 4
#n_reason_start = 3
#n_reason_end = 3

def skip_model_5_mtsk_att(cell_size = 350):

    input_data_context_id = Input(shape=[10], name="context")
    input_data_start_id = Input(shape=[10], name="start")
    input_data_end_id = Input(shape=[10], name="end")
    input_data = Input(shape=[10,input_fea_dim], name="input_fea")
    output_data_i = Input(shape=[10], name="output_fea")
    input_id = Input(shape=[10], name="input_id")
    output_id = Input(shape=[10], name="output_id")

    song_emb_layer = Embedding(
        input_dim=spotify_song_array.shape[0],
        output_dim=spotify_song_array.shape[1],
        weights=[spotify_song_array],
        trainable=False
    )

    context_emb_layer = Embedding(n_context_type,25)
    reason_start_emb_layer = Embedding(n_reason_start,25)
    reason_end_emb_layer = Embedding(n_reason_end,25)

    emb_input_id = song_emb_layer(input_id)
    emb_output_id = song_emb_layer(output_id)
    emb_input_data_context_id = context_emb_layer(input_data_context_id)
    emb_input_data_start_id = reason_start_emb_layer(input_data_start_id)
    emb_input_data_end_id = reason_end_emb_layer(input_data_end_id)

    input_data_a = concatenate([input_data,emb_input_id,emb_input_data_context_id,
                              emb_input_data_start_id,emb_input_data_end_id])

    # rnn layers
#    encoder_outputs, state_h
    
    encoder_outputs, rnn_layer = GRU(cell_size, return_sequences=True, return_state=True) (input_data_a)
    
    encoder_outputs_1, rnn_layer_1 = GRU(cell_size, return_sequences=True, return_state=True) (encoder_outputs)
    
    #rnn_layer_5 = Lambda(exp_smooth5)(encoder_outputs)    
    #rnn_layer_8 = Lambda(exp_smooth8)(encoder_outputs)    
#    print(encoder_outputs.shape)
#    print(rnn_layer_5.shape)
#    print(rnn_layer.shape)

    
    rnn_layer = concatenate([rnn_layer, rnn_layer_1])
    
    output_data = Reshape([10,1])(output_data_i)
    
    output_data = concatenate([output_data, emb_output_id])

    output_data = Dense(2*cell_size, activation='relu')(output_data)

    rnn_layer_multi = Multiply()([output_data, rnn_layer])
    
    rnn_layer_reshape = Reshape([1,2*cell_size])(rnn_layer)
    
    rnn_layer_reshape = Lambda(tile_tile)(rnn_layer_reshape)

    output_result = concatenate([rnn_layer_reshape, rnn_layer_multi, output_data])
    
    output_rnn_layer = Bidirectional(GRU(cell_size, return_sequences=True))(output_result)
    
    output_rnn_layer_2 = Bidirectional(GRU(cell_size, return_sequences=True))(output_rnn_layer)
    
    output_rnn_layer_3 = Bidirectional(GRU(200, return_sequences=True))(output_rnn_layer_2)
    
    output_rnn_layer_4 = Bidirectional(GRU(200, return_sequences=True))(output_rnn_layer_3)
    
    output_result = concatenate([output_result, output_rnn_layer, output_rnn_layer_2, output_rnn_layer_3, output_rnn_layer_4])

    output_result = Dense(1000, activation='relu')(output_result)
    output_result_1 = Dense(784, activation='relu')(output_result)
    #output_result_2 = Dense(784, activation='elu')(output_result_1)
    
    #output_result = concatenate([output_result, output_result_1, output_result_2])
    
    output_result = Dropout(0.2)(output_result_1)

    output_result = Dense(11, activation='sigmoid')(output_result)
    
    #output_result = Reshape([10])(output_result)


    model = Model(inputs=[input_data_context_id, input_data_start_id,
                          input_data_end_id, input_data, output_data_i, input_id, output_id], outputs=output_result)

    sgd = Adam(lr=0.0008)
    model.compile(loss='binary_crossentropy',
                  optimizer=sgd,
                  metrics=['binary_crossentropy', 'binary_accuracy'])
    model.summary()
    return model

checkpoint = ModelCheckpoint('Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5', monitor='val_binary_accuracy', verbose=1, save_best_only=True, mode='auto')

#K.clear_session()

model = skip_model_5_mtsk_att()

reduceLROnPlat = ReduceLROnPlateau(monitor='val_loss', factor=0.8, patience=4, 
                                   verbose=1, mode='auto', epsilon=0.0001, cooldown=5, min_lr=0.0001)

model.fit_generator(train_generate(), steps_per_epoch=3000, epochs=300, verbose=1,
                        validation_data=(X_valid,Y_valid),max_q_size=35,
                      callbacks = [mstk_ndcg_callback(),reduceLROnPlat,checkpoint])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_id (InputLayer)           (None, 10)           0                                            
__________________________________________________________________________________________________
context (InputLayer)            (None, 10)           0                                            
__________________________________________________________________________________________________
start (InputLayer)              (None, 10)           0                                            
__________________________________________________________________________________________________
end (InputLayer)                (None, 10)           0                                            
__________________________________________________________________________________________________
input_fea 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:1065: UserWarning: `epsilon` argument is deprecated and will be removed, use `min_delta` instead.
  warnings.warn('`epsilon` argument is deprecated and '
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:188: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., epochs=300, max_queue_size=35, validation_data=({'context..., callbacks=[<__main__..., steps_per_epoch=3000, verbose=1)`


Epoch 1/300
3000/3000 [==============================] - 1735s 578ms/step - loss: 0.2789 - binary_crossentropy: 0.2789 - binary_accuracy: 0.8734 - val_loss: 0.2821 - val_binary_crossentropy: 0.2821 - val_binary_accuracy: 0.8721
0.7508228055989036

Epoch 00001: val_binary_accuracy improved from -inf to 0.87209, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5
Epoch 2/300
3000/3000 [==============================] - 1740s 580ms/step - loss: 0.2633 - binary_crossentropy: 0.2633 - binary_accuracy: 0.8809 - val_loss: 0.2773 - val_binary_crossentropy: 0.2773 - val_binary_accuracy: 0.8743
0.7556039821812296

Epoch 00002: val_binary_accuracy improved from 0.87209 to 0.87428, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5
Epoch 3/300
3000/3000 [==============================] - 1837s 612ms/step - loss: 0.2598 - binary_crossentropy: 0.2598 - binary_accuracy: 0.8826 - val_loss: 0.2745 - val_binary_crossentropy: 0.2745 - val_binary_accuracy: 0.8757
0.75878

3000/3000 [==============================] - 1815s 605ms/step - loss: 0.2520 - binary_crossentropy: 0.2520 - binary_accuracy: 0.8863 - val_loss: 0.2682 - val_binary_crossentropy: 0.2682 - val_binary_accuracy: 0.8787
0.7643524338556638

Epoch 00024: val_binary_accuracy improved from 0.87834 to 0.87865, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5
Epoch 25/300
3000/3000 [==============================] - 1822s 607ms/step - loss: 0.2517 - binary_crossentropy: 0.2517 - binary_accuracy: 0.8866 - val_loss: 0.2678 - val_binary_crossentropy: 0.2678 - val_binary_accuracy: 0.8787
0.764826660088619

Epoch 00025: val_binary_accuracy improved from 0.87865 to 0.87875, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5
Epoch 26/300
3000/3000 [==============================] - 1824s 608ms/step - loss: 0.2518 - binary_crossentropy: 0.2518 - binary_accuracy: 0.8864 - val_loss: 0.2680 - val_binary_crossentropy: 0.2680 - val_binary_accuracy: 0.8787
0.7646987047489

3000/3000 [==============================] - 1876s 625ms/step - loss: 0.2490 - binary_crossentropy: 0.2490 - binary_accuracy: 0.8878 - val_loss: 0.2659 - val_binary_crossentropy: 0.2659 - val_binary_accuracy: 0.8797
0.7670441129331189

Epoch 00048: val_binary_accuracy did not improve from 0.87988
Epoch 49/300
3000/3000 [==============================] - 1836s 612ms/step - loss: 0.2488 - binary_crossentropy: 0.2488 - binary_accuracy: 0.8879 - val_loss: 0.2651 - val_binary_crossentropy: 0.2651 - val_binary_accuracy: 0.8801
0.7675381260742642

Epoch 00049: val_binary_accuracy improved from 0.87988 to 0.88006, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5
Epoch 50/300
3000/3000 [==============================] - 1757s 586ms/step - loss: 0.2495 - binary_crossentropy: 0.2495 - binary_accuracy: 0.8875 - val_loss: 0.2653 - val_binary_crossentropy: 0.2653 - val_binary_accuracy: 0.8800
0.7672512159055083

Epoch 00050: val_binary_accuracy did not improve from 0.88006
Epoch 

...

3000/3000 [==============================] - 1845s 615ms/step - loss: 0.2465 - binary_crossentropy: 0.2465 - binary_accuracy: 0.8888 - val_loss: 0.2619 - val_binary_crossentropy: 0.2619 - val_binary_accuracy: 0.8816
0.7704441633237784

Epoch 00144: val_binary_accuracy did not improve from 0.88161
Epoch 145/300
3000/3000 [==============================] - 1853s 618ms/step - loss: 0.2456 - binary_crossentropy: 0.2456 - binary_accuracy: 0.8894 - val_loss: 0.2622 - val_binary_crossentropy: 0.2622 - val_binary_accuracy: 0.8814
0.7703155484205431

Epoch 00145: val_binary_accuracy did not improve from 0.88161
Epoch 146/300
3000/3000 [==============================] - 1821s 607ms/step - loss: 0.2458 - binary_crossentropy: 0.2458 - binary_accuracy: 0.8892 - val_loss: 0.2622 - val_binary_crossentropy: 0.2622 - val_binary_accuracy: 0.8815
0.7702304647153257

Epoch 00146: val_binary_accuracy did not improve from 0.88161
Epoch 147/300
3000/3000 [==============================] - 1827s 609ms/step - 

/usr/local/lib/python3.5/dist-packages/keras/callbacks.py:122: UserWarning: Method on_batch_end() is slow compared to the batch update (0.600149). Check your callbacks.
  % delta_t_median)


3000/3000 [==============================] - 1829s 610ms/step - loss: 0.2463 - binary_crossentropy: 0.2463 - binary_accuracy: 0.8890 - val_loss: 0.2616 - val_binary_crossentropy: 0.2616 - val_binary_accuracy: 0.8817
0.7705602465184935

Epoch 00156: val_binary_accuracy improved from 0.88168 to 0.88169, saving model to Data/skip_net_glove_max_mtsk_more_layer_best_v6.hdf5
Epoch 157/300
3000/3000 [==============================] - 1819s 606ms/step - loss: 0.2462 - binary_crossentropy: 0.2462 - binary_accuracy: 0.8890 - val_loss: 0.2619 - val_binary_crossentropy: 0.2619 - val_binary_accuracy: 0.8816
0.7704936305942536

Epoch 00157: val_binary_accuracy did not improve from 0.88169
Epoch 158/300
3000/3000 [==============================] - 1799s 600ms/step - loss: 0.2458 - binary_crossentropy: 0.2458 - binary_accuracy: 0.8893 - val_loss: 0.2622 - val_binary_crossentropy: 0.2622 - val_binary_accuracy: 0.8815
0.7703551222369232

Epoch 00158: val_binary_accuracy did not improve from 0.88169
Epoc

3000/3000 [==============================] - 1832s 611ms/step - loss: 0.2453 - binary_crossentropy: 0.2453 - binary_accuracy: 0.8895 - val_loss: 0.2618 - val_binary_crossentropy: 0.2618 - val_binary_accuracy: 0.8816
0.7702739959133439

Epoch 00182: val_binary_accuracy did not improve from 0.88173
Epoch 183/300
3000/3000 [==============================] - 1808s 603ms/step - loss: 0.2463 - binary_crossentropy: 0.2463 - binary_accuracy: 0.8890 - val_loss: 0.2620 - val_binary_crossentropy: 0.2620 - val_binary_accuracy: 0.8816
0.7703993129985477

Epoch 00183: val_binary_accuracy did not improve from 0.88173
Epoch 184/300
1070/3000 [=========>....................] - ETA: 19:30 - loss: 0.2461 - binary_crossentropy: 0.2461 - binary_accuracy: 0.8891

KeyboardInterrupt: 